# Battle of the Neighborhoods Project: 
## Using Data Science Methods To Determine Optimal Locations for Expanding a Cocktail Bar Business

### Data

**Sources of Data**

 - **Dataset containing the neighborhood names and postal codes in Toronto**
 
     - Source:  This data is available in the form of a wikipedia table at the link:  https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
     - Description of dataset:  The dataset contains information about postal codes, boroughs, and neighborhoods.
     - Data wrangling requirements:  The BeautifulSoup package in Python will be used to scraped the information from the Wikipedia table and convert it into a pandas dataframe.   
     
     
 - **Dataset containing latitude and longitude coordinates to merge with the Toronto postal codes** 
     - Source:  This data is available from the following link:  https://cocl.us/Geospatial_data
     - Description of dataset:  The dataset contains the postal codes and the corresponding latitiude and longitude coordinates.
     - Data wrangling requirements:  An inner left join on the postal code column will be performed.  

 
 
  - **Dataframe containing the latitude and longitude coordinates of each neighborhood in Toronto**
     - Source: The information scraped from the Wikipedia page containing neighborhood information and postal codes will be merged with geospatial data containing the postal codes along with the latitude and longitude coordinates.
     - Description of dataset:  Contains information about postal codes, neighborhoods and the corresponding latitude and longitude coordinates.
     - Data wrangling requirements:  I will create a subset of the dataframe limiting rows with strings containing the word Toronto.  I will groupby post code and borough, and then apply and join the neighborhoods, separated by a comma, in the same row as other neighborhoods in the postal code.
     
     
   - **Foursquare API Venue Data for Toronto used to create a dataframe with information about the venues contained within each Toronto neighborhood**
     - Source:  I'll create a variable called url to connect to the foursquare api and return a json file, using the following link:  https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format  I'll pass through the client ID, client secret, vewrsion, lat, lng, radius, and limit.
     - Description of dataset:  Information about nearby venues, including neighborhood names, latitude, longitude, venue name, venue latitude and longitude, venue category.
     - Data wrangling requirements:  I'll make the get request and run a function to return information for each Toronto neighborhood into a dataframe.
 

 - **Dataframe showing the top 10 most common venues in each Toronto neighborhood**
     - Source: I will start with the dataframe containing information about the venues contained within each Toronto neighborhood.
     - Description of dataset: A dataframe showing the top 10 venues in each neighborhood, in order from the 1st most popular to the 10th.
     - Data wrangling requirements:  I will perform one hot encoding to represent the categorical variables as binary vectors and then groupby means, and determine the frequency of the venues in each neighborhood.


     
 - **Dataframe showing a count of the existing bars in each Toronto neighborhood**
     - Source: Started with dataframe containing information about the venues contained within each Toronto neighborhood.
     - Description of dataset:  Contains a count of the number of bars in each Toronto neighborhood.
     - Data wrangling requirements:  I will create a dataframe with rows containing the strings Pub, pub, bar, Bar, or Speakeasy, and remove any rows that describe barbershops, juice bars, or hookah bars.
     


 - **After performing the above data science activities on the Toronto data, I will perform similar actions to produce dataframes containing Manhattan data, and then I will merge the two dataframes to enable clustering analysis on the combined dataframe.**
     - The New York neighbood data can be found at the following link: https://geo.nyu.edu/catalog/nyu_2451_34572
     - After merging the Toronto and New York dataframes, it is likely that there will be some venue categories present in one city and not the other.  I'll need to replace any not a number (NaN) values in the dataframe with zeroes to enable the clustering analysis.

**Description of How the Data Will Be Used to Solve the Problem**

I will use the k means clustering unsupervised machine learning algorithm to identify k number of centroids, and then allocate every Toronto neighborhood to the nearest cluster, while keeping the centroids as small as possible.  I will assign each of the Toronto neighborhoods to one of five clusters, containing neighborhoods that are more similar to each other than to neighborhoods in the other clusters, based on the venue data acquired via the FourSquare API.  This will help the data scientist and the bar owners to identify another Toronto neighborhood location to open a bar in, which is similar to the existing bar location of Kensington Market.

I will use the k means clustering algorithm again on the Manhattan neighborhood dataframe, and then again on the dataframe that combines both Toronto and Manhattan venue information by neighborhood.  This will allow me to determine which Manhattan neighborhoods are similar to the Toronto neighborhood of Kensington Market, as evidenced by the neighborhoods appearing in the same cluster produded by the unsupervised machine learning algorithm.

After identifying neighborhoods similar to Kensington Market, in both Toronto and Manhattan, I will review the data summarizing the number of existing bars in each neighborhood, to confirm that there is sufficient interest to open a bar and to rule out any neighborhoods that may be too saturated with existing bars (e.g. more than 10 bars).  Then the data scientist will be able to make recommendations to the bar owners, and the bar owners will be able to demonstrate, to their bank loan officer, that they have done their homework to identify new bar locations that are optimal for continued business success.

Import of libraries

In [2]:
import pandas as pd  # library for data analsysis

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import numpy as np  # library to handle data in a vectorized manner
from bs4 import BeautifulSoup
import requests

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/DSX-Python35

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.0.2r             |       h14c3975_0         3.1 MB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    certifi-2018.8.24          |        py35_1001         139 KB  conda-forge
    ca-certificates-2019.3.9   |       hecc5488_0         146 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.49-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

   

Code to scrape contents from Wikipedia table of Canadian postal codes, and then to wrangle the data.  This section also includes code to acquire geospatial data and then join it to the Canadian postal code data frame.

In [7]:
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
response = requests.get(url)
soup = BeautifulSoup(response.text, 'lxml')

table = soup.find_all('table', class_='sortable')
table = table[0]
table_rows = table.find_all('tr')
data = []
for row in table_rows:
    data.append([t.text.strip() for t in row.find_all('td')])
df = pd.DataFrame(data, columns=['PostalCode', 'Borough', 'Neighbourhood'])
new_df = df[df.Borough != 'Not assigned']
new_df1 = new_df[~new_df['Borough'].isnull()]
new_df2 = new_df1.reset_index(drop=True)
new_df3 = new_df2.groupby(['PostalCode', 'Borough'])['Neighbourhood'].apply(', '.join).reset_index()
new_df3.loc[new_df3['Neighbourhood'] == 'Not assigned']
new_df3.loc[new_df3.Neighbourhood == 'Not assigned', 'Neighbourhood'] = new_df3['Borough']

latlongdf = pd.read_csv("https://cocl.us/Geospatial_data")
df_cd = pd.merge(new_df3, latlongdf, how='inner', left_on = 'PostalCode', right_on = 'Postal Code')
df_cd1 = df_cd.drop(['Postal Code'], axis=1)

df_cd1.head()

PostalCode      Borough                           Neighbourhood   Latitude  \
0        M1B  Scarborough                          Rouge, Malvern  43.806686   
1        M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [8]:
df_cd1.shape

(103, 5)

Items required to perform clustering analysis.

In [9]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json # library to handle JSON files
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
# import k-means from clustering stage
from sklearn.cluster import KMeans
!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library
import folium # map rendering library
print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Libraries imported.


Narrow down the dataset to Toronto.

In [10]:
Torontodf = df_cd1[df_cd1['Borough'].str.contains('Toronto')].reset_index(drop=True)

In [11]:
#Get the geographical location of Toronto
address = 'Toronto, CAN'

geolocator = Nominatim(user_agent="Toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map of Toronto using latitude and longitude values
map_Toronto = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(Torontodf['Latitude'], Torontodf['Longitude'], Torontodf['Neighbourhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Toronto)  
    
map_Toronto

Foursquare details.

In [12]:
CLIENT_ID = '1YIGHKEQNF3RB4KKN0HFHIMEO2IGG5OD53WYTZACPOXKCQJZ' # your Foursquare ID
CLIENT_SECRET = 'JZKJHWBNLIHXZPGMC1NOFZKRMI3WCFVDLXIRVKNUUDT4PSMS' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 1YIGHKEQNF3RB4KKN0HFHIMEO2IGG5OD53WYTZACPOXKCQJZ
CLIENT_SECRET:JZKJHWBNLIHXZPGMC1NOFZKRMI3WCFVDLXIRVKNUUDT4PSMS


Limit the number of venues returned by the Foursquare API, define the radius of venues. Create a function to identify the top 100 venues that are in each neighborhood within a radius of 500 meters, and a function to get the category type of the venues.  Then clean the json and bring it into a pandas dataframe.

In [13]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Code to run the above function on each neighborhood and create a new dataframe called Toronto_venues.

In [14]:
Toronto_venues = getNearbyVenues(names=Torontodf['Neighbourhood'],
                                   latitudes=Torontodf['Latitude'],
                                   longitudes=Torontodf['Longitude']
                                  )

The Beaches
The Danforth West, Riverdale
The Beaches West, India Bazaar
Studio District
Lawrence Park
Davisville North
North Toronto West
Davisville
Moore Park, Summerhill East
Deer Park, Forest Hill SE, Rathnelly, South Hill, Summerhill West
Rosedale
Cabbagetown, St. James Town
Church and Wellesley
Harbourfront, Regent Park
Ryerson, Garden District
St. James Town
Berczy Park
Central Bay Street
Adelaide, King, Richmond
Harbourfront East, Toronto Islands, Union Station
Design Exchange, Toronto Dominion Centre
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North, Forest Hill West
The Annex, North Midtown, Yorkville
Harbord, University of Toronto
Chinatown, Grange Park, Kensington Market
CN Tower, Bathurst Quay, Island airport, Harbourfront West, King and Spadina, Railway Lands, South Niagara
Stn A PO Boxes 25 The Esplanade
First Canadian Place, Underground city
Christie
Dovercourt Village, Dufferin
Little Portugal, Trinity
Brockton, Exhibition Place, Parkdale Village
High Park, The 

Take a look at the resulting dataframe.

In [15]:
print(Toronto_venues.shape)
Toronto_venues.head()

(1696, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  The Beaches              43.676357              -79.293031   
1  The Beaches              43.676357              -79.293031   
2  The Beaches              43.676357              -79.293031   
3  The Beaches              43.676357              -79.293031   
4  The Beaches              43.676357              -79.293031   

                                Venue  Venue Latitude  Venue Longitude  \
0  The Big Carrot Natural Food Market       43.678879       -79.297734   
1                 Grover Pub and Grub       43.679181       -79.297215   
2                 Guru Raghavendra Ji       43.680187       -79.292337   
3  The Big Carrot Natural Food Market       43.678730       -79.297478   
4                       Upper Beaches       43.680563       -79.292869   

      Venue Category  
0  Health Food Store  
1                Pub  
2         Astrologer  
3      Grocery Store  
4       Neighborhood

In [16]:
Toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide, King, Richmond                                              100   
Berczy Park                                                            55   
Brockton, Exhibition Place, Parkdale Village                           20   
Business Reply Mail Processing Centre 969 Eastern                      17   
CN Tower, Bathurst Quay, Island airport, Harbou...                     15   
Cabbagetown, St. James Town                                            46   
Central Bay Street                                                     87   
Chinatown, Grange Park, Kensington Market                             100   
Christie                                                               16   
Church and Wellesley                                                   86   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             36   
Davisville North                                                        6   
Deer Park, Forest Hill SE, Rathnelly, South Hil...                     14   
Design Exchange, Toronto Dominion Centre                              100   
Dovercourt Village, Dufferin                                           19   
First Canadian Place, Underground city                                100   
Forest Hill North, Forest Hill West                                     4   
Harbord, University of Toronto                                         35   
Harbourfront East, Toronto Islands, Union Station                     100   
Harbourfront, Regent Park                                              46   
High Park, The Junction South                                          23   
Lawrence Park                                                           3   
Little Portugal, Trinity                                               62   
Moore Park, Summerhill East                                             4   
North Toronto West                                                     20   
Parkdale, Roncesvalles                                                 15   
Rosedale                                                                4   
Roselawn                                                                2   
Runnymede, Swansea                                                     39   
Ryerson, Garden District                                              100   
St. James Town                                                        100   
Stn A PO Boxes 25 The Esplanade                                        94   
Studio District                                                        37   
The Annex, North Midtown, Yorkville                                    23   
The Beaches                                                             5   
The Beaches West, India Bazaar                                         21   
The Danforth West, Riverdale                                           42   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Adelaide, King, Richmond                                               100   
Berczy Park                                                             55   
Brockton, Exhibition Place, Parkdale Village                            20   
Business Reply Mail Processing Centre 969 Eastern                       17   
CN Tower, Bathurst Quay, Island airport, Harbou...                      15   
Cabbagetown, St. James Town                                             46   
Central Bay Street                                                      87   
Chinatown, Grange Park, Kensington Market                              100   
Christie                                                                16   
Church and Wellesley                                                    86   
Commerce Court, Victoria Hotel     

In [17]:
print('There are {} uniques categories.'.format(len(Toronto_venues['Venue Category'].unique())))

There are 235 uniques categories.


In [18]:
# one hot encoding
Toronto_onehot = pd.get_dummies(Toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Toronto_onehot['Neighborhood'] = Toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Toronto_onehot.columns[-1]] + list(Toronto_onehot.columns[:-1])
Toronto_onehot = Toronto_onehot[fixed_columns]

Toronto_onehot.head()

Yoga Studio  Adult Boutique  Afghan Restaurant  Airport  \
0            0               0                  0        0   
1            0               0                  0        0   
2            0               0                  0        0   
3            0               0                  0        0   
4            0               0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Astrologer  \
0           0                    0                 0           0   
1           0                    0                 0           0   
2           0                    0                 0           1   
3           0                    0                 0           0   
4           0                    0                 0           0   

   Athletics & Sports  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                   0          0           0           0       0     0    0   
1                   0          0           0           0       0     0    0   
2                   0          0           0           0       0     0    0   
3                   0          0           0           0       0     0    0   
4                   0          0           0           0       0     0    0   

   Baseball Stadium  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0                 0                   0      0                0         0   
1                 0                   0      0                0         0   
2                 0                   0      0                0         0   
3                 0                   0      0                0         0   
4                 0                   0      0                0         0   

   Beer Store  Belgian Restaurant  Bistro  Boat or Ferry  Bookstore  Boutique  \
0           0                   0       0              0          0         0   
1           0                   0       0              0          0         0   
2           0                   0       0              0          0         0   
3           0                   0       0              0          0         0   
4           0                   0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  \
0                     0               0        0                0   
1                     0               0        0                0   
2                     0               0        0                0   
3                     0               0        0                0   
4                     0               0        0                0   

   Burger Joint  Burrito Place  Bus Line  Butcher  Café  \
0             0              0         0        0     0   
1             0              0         0        0     0   
2             0              0         0        0     0   
3             0              0         0        0     0   
4             0              0         0        0     0   

   Cajun / Creole Restaurant  Camera Store  Caribbean Restaurant  Cheese Shop  \
0                        

In [19]:
Toronto_onehot.shape

(1696, 235)

In [21]:
Toronto_grouped = Toronto_onehot.groupby('Neighborhood').mean().reset_index()
Toronto_grouped

Neighborhood  Yoga Studio  \
0                            Adelaide, King, Richmond     0.000000   
1                                         Berczy Park     0.000000   
2        Brockton, Exhibition Place, Parkdale Village     0.000000   
3   Business Reply Mail Processing Centre 969 Eastern     0.000000   
4   CN Tower, Bathurst Quay, Island airport, Harbo...     0.000000   
5                         Cabbagetown, St. James Town     0.000000   
6                                  Central Bay Street     0.011494   
7           Chinatown, Grange Park, Kensington Market     0.000000   
8                                            Christie     0.000000   
9                                Church and Wellesley     0.011628   
10                     Commerce Court, Victoria Hotel     0.000000   
11                                         Davisville     0.000000   
12                                   Davisville North     0.000000   
13  Deer Park, Forest Hill SE, Rathnelly, South Hi...     0.000000   
14           Design Exchange, Toronto Dominion Centre     0.000000   
15                       Dovercourt Village, Dufferin     0.000000   
16             First Canadian Place, Underground city     0.000000   
17                Forest Hill North, Forest Hill West     0.000000   
18                     Harbord, University of Toronto     0.028571   
19  Harbourfront East, Toronto Islands, Union Station     0.000000   
20                          Harbourfront, Regent Park     0.021739   
21                      High Park, The Junction South     0.000000   
22                                      Lawrence Park     0.000000   
23                           Little Portugal, Trinity     0.016129   
24                        Moore Park, Summerhill East     0.000000   
25                                 North Toronto West     0.050000   
26                             Parkdale, Roncesvalles     0.000000   
27                                           Rosedale     0.000000   
28                                           Roselawn     0.000000   
29                                 Runnymede, Swansea     0.000000   
30                           Ryerson, Garden District     0.000000   
31                                     St. James Town     0.000000   
32                    Stn A PO Boxes 25 The Esplanade     0.000000   
33                                    Studio District     0.027027   
34                The Annex, North Midtown, Yorkville     0.000000   
35                                        The Beaches     0.000000   
36                     The Beaches West, India Bazaar     0.000000   
37                       The Danforth West, Riverdale     0.023810   

    Adult Boutique  Afghan Restaurant   Airport  Airport Food Court  \
0         0.000000           0.000000  0.000000            0.000000   
1         0.000000           0.000000  0.000000            0.000000   
2         0.000000           0.000000  0.000000            0.000000   
3         0.000000           0.000000  0.000000            0.000000   
4         0.000000           0.000000  0.066667            0.066667   
5         0.000000           0.000000  0.000000            0.000000   
6         0.000000           0.000000  0.000000            0.000000   
7         0.000000           0.000000  0.000000            0.000000   
8         0.000000           0.000000  0.000000            0.000000   
9         0.011628           0.011628  0.000000            0.000000   
10        0.000000           0.000000  0.000000            0.000000   
11        0.000000           0.000000  0.000000            0.000000   
12        0.000000           0.000000  0.000000            0.000000   
13        0.000000           0.000000  0.000000            0.000000   
14        0.000000           0.000000  0.000000            0.000000   
15        0.000000           0.000000  0.000000            0.000000   
16        0.000000           0.000000  0.000000            0.000000   
17        0.000000           0.0

In [22]:
Toronto_grouped.shape

(38, 235)

In [23]:
num_top_venues = 5

for hood in Toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = Toronto_grouped[Toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide, King, Richmond----
                 venue  freq
0          Coffee Shop  0.06
1                 Café  0.05
2  American Restaurant  0.04
3           Steakhouse  0.04
4                  Bar  0.04


----Berczy Park----
                venue  freq
0         Coffee Shop  0.07
1        Cocktail Bar  0.05
2  Italian Restaurant  0.04
3      Farmers Market  0.04
4            Beer Bar  0.04


----Brockton, Exhibition Place, Parkdale Village----
                  venue  freq
0        Breakfast Spot  0.10
1                  Café  0.10
2           Coffee Shop  0.10
3                Bakery  0.05
4  Caribbean Restaurant  0.05


----Business Reply Mail Processing Centre 969 Eastern----
                venue  freq
0  Light Rail Station  0.12
1          Comic Shop  0.06
2    Recording Studio  0.06
3             Brewery  0.06
4         Pizza Place  0.06


----CN Tower, Bathurst Quay, Island airport, Harbourfront West, King and Spadina, Railway Lands, South Niagara----
              venue  fr

In [24]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [25]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
tneighborhoods_venues_sorted = pd.DataFrame(columns=columns)
tneighborhoods_venues_sorted['Neighborhood'] = Toronto_grouped['Neighborhood']

for ind in np.arange(Toronto_grouped.shape[0]):
    tneighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Toronto_grouped.iloc[ind, :], num_top_venues)

tneighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                           Adelaide, King, Richmond           Coffee Shop   
1                                        Berczy Park           Coffee Shop   
2       Brockton, Exhibition Place, Parkdale Village        Breakfast Spot   
3  Business Reply Mail Processing Centre 969 Eastern    Light Rail Station   
4  CN Tower, Bathurst Quay, Island airport, Harbo...       Airport Service   

  2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
0                  Café            Steakhouse    American Restaurant   
1          Cocktail Bar    Italian Restaurant            Cheese Shop   
2                  Café           Coffee Shop  Performing Arts Venue   
3           Pizza Place                Garden             Skate Park   
4        Airport Lounge      Airport Terminal                  Plane   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                   Bar       Thai Restaurant        Cosmetics Shop   
1                  Café        Farmers Market            Steakhouse   
2            Restaurant                   Bar  Caribbean Restaurant   
3                  Park        Farmers Market                   Spa   
4         Boat or Ferry      Sculpture Garden              Boutique   

  8th Most Common Venue   9th Most Common Venue 10th Most Common Venue  
0                 Hotel            Burger Joint                 Bakery  
1            Restaurant                  Bakery     Seafood Restaurant  
2               Stadium  Furniture / Home Store     Italian Restaurant  
3  Fast Food Restaurant                 Brewery          Burrito Place  
4          Airport Gate                 Airport        Harbor / Marina

In [26]:
# set number of clusters
kclusters = 5

Toronto_grouped_clustering = Toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 3, 3, 3, 3, 3, 3, 3, 3, 3], dtype=int32)

In [27]:
# add clustering labels
tneighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

In [28]:
Toronto_merged = Torontodf

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
Toronto_merged = Toronto_merged.join(tneighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighbourhood')

Toronto_merged.head() # check the last columns!

PostalCode          Borough                   Neighbourhood   Latitude  \
0        M4E     East Toronto                     The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2        M4L     East Toronto  The Beaches West, India Bazaar  43.668999   
3        M4M     East Toronto                 Studio District  43.659526   
4        M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0 -79.293031               4     Health Food Store         Grocery Store   
1 -79.352188               3      Greek Restaurant           Coffee Shop   
2 -79.315572               3        Sandwich Place                  Park   
3 -79.340923               3                  Café           Coffee Shop   
4 -79.388790               2                  Park           Swim School   

  3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0            Astrologer                   Pub           Women's Store   
1        Ice Cream Shop    Italian Restaurant  Furniture / Home Store   
2                   Gym            Steakhouse       Food & Drink Shop   
3             Gastropub                Bakery      Italian Restaurant   
4              Bus Line         Women's Store          Discount Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0   Dumpling Restaurant        Discount Store               Dog Run   
1           Yoga Studio             Bookstore               Brewery   
2     Fish & Chips Shop  Fast Food Restaurant               Brewery   
3   American Restaurant           Yoga Studio               Brewery   
4        Farmers Market    Falafel Restaurant           Event Space   

  9th Most Common Venue 10th Most Common Venue  
0      Doner Restaurant             Donut Shop  
1       Bubble Tea Shop                   Café  
2          Burger Joint          Burrito Place  
3    Seafood Restaurant         Sandwich Place  
4  Ethiopian Restaurant      Electronics Store

In [29]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Toronto_merged['Latitude'], Toronto_merged['Longitude'], Toronto_merged['Neighbourhood'], Toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [25]:
Toronto_merged.loc[Toronto_merged['Cluster Labels'] == 0, Toronto_merged.columns[[2] + list(range(5, Toronto_merged.shape[1]))]]

Neighbourhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
22      Roselawn               0        Ice Cream Shop                Garden   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
22         Women's Store        Discount Store  Fast Food Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
22        Farmers Market    Falafel Restaurant           Event Space   

   9th Most Common Venue 10th Most Common Venue  
22  Ethiopian Restaurant      Electronics Store

In [26]:
Toronto_merged.loc[Toronto_merged['Cluster Labels'] == 1, Toronto_merged.columns[[2] + list(range(5, Toronto_merged.shape[1]))]]

Neighbourhood  Cluster Labels 1st Most Common Venue  \
8           Moore Park, Summerhill East               1            Playground   
10                             Rosedale               1                  Park   
23  Forest Hill North, Forest Hill West               1                  Park   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
8                   Park          Tennis Court                 Trail   
10            Playground                 Trail         Women's Store   
23                 Trail      Sushi Restaurant         Jewelry Store   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
8          Women's Store   Dumpling Restaurant        Discount Store   
10          Dessert Shop    Falafel Restaurant           Event Space   
23         Women's Store        Discount Store        Farmers Market   

   8th Most Common Venue 9th Most Common Venue       10th Most Common Venue  
8                Dog Run      Doner Restaurant                   Donut Shop  
10  Ethiopian Restaurant     Electronics Store  Eastern European Restaurant  
23    Falafel Restaurant           Event Space         Ethiopian Restaurant

In [27]:
Toronto_merged.loc[Toronto_merged['Cluster Labels'] == 2, Toronto_merged.columns[[2] + list(range(5, Toronto_merged.shape[1]))]]

Neighbourhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
4  Lawrence Park               2                  Park           Swim School   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
4              Bus Line         Women's Store        Discount Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
4        Farmers Market    Falafel Restaurant           Event Space   

  9th Most Common Venue 10th Most Common Venue  
4  Ethiopian Restaurant      Electronics Store

In [29]:
Toronto_merged.loc[Toronto_merged['Cluster Labels'] == 3, Toronto_merged.columns[[2] + list(range(5, Toronto_merged.shape[1]))]]

Neighbourhood  Cluster Labels  \
1                        The Danforth West, Riverdale               3   
2                      The Beaches West, India Bazaar               3   
3                                     Studio District               3   
5                                    Davisville North               3   
6                                  North Toronto West               3   
7                                          Davisville               3   
9   Deer Park, Forest Hill SE, Rathnelly, South Hi...               3   
11                        Cabbagetown, St. James Town               3   
12                               Church and Wellesley               3   
13                          Harbourfront, Regent Park               3   
14                           Ryerson, Garden District               3   
15                                     St. James Town               3   
16                                        Berczy Park               3   
17                                 Central Bay Street               3   
18                           Adelaide, King, Richmond               3   
19  Harbourfront East, Toronto Islands, Union Station               3   
20           Design Exchange, Toronto Dominion Centre               3   
21                     Commerce Court, Victoria Hotel               3   
24                The Annex, North Midtown, Yorkville               3   
25                     Harbord, University of Toronto               3   
26          Chinatown, Grange Park, Kensington Market               3   
27  CN Tower, Bathurst Quay, Island airport, Harbo...               3   
28                    Stn A PO Boxes 25 The Esplanade               3   
29             First Canadian Place, Underground city               3   
30                                           Christie               3   
31                       Dovercourt Village, Dufferin               3   
32                           Little Portugal, Trinity               3   
33       Brockton, Exhibition Place, Parkdale Village               3   
34                      High Park, The Junction South               3   
35                             Parkdale, Roncesvalles               3   
36                                 Runnymede, Swansea               3   
37  Business Reply Mail Processing Centre 969 Eastern               3   

   1st Most Common Venue          2nd Most Common Venue 3rd Most Common Venue  \
1       Greek Restaurant                    Coffee Shop        Ice Cream Shop   
2         Sandwich Place                           Park                   Gym   
3                   Café                    Coffee Shop             Gastropub   
5         Breakfast Spot                 Sandwich Place                   Gym   
6         Clothing Store                    Coffee Shop           Yoga Studio   
7            Pizza Place                   Dessert Shop        Sandwich Place   
9            Coffee Shop                            Pub           Pizza Place   
11           Coffee Shop                           Park            Restaurant   
12           Coffee Shop            Japanese Restaurant      Sushi Restaurant   
13           Coffee Shop                            Pub                Bakery   
14           Coffee Shop                 Clothing Store                  Café   
15           Coffee Shop                           Café            Restaurant   
16           Coffee Shop                   Cocktail Bar    Italian Restaurant   
17           Coffee Shop                           Café    Italian Restaurant   
18           Coffee Shop                           Café            Steakhouse   
19           Coffee Shop                          Hotel              Aquarium   
20           Coffee Shop                           Café                 Hotel   
21           Coffee Shop                           Café                 Hotel   
24           Coffee Shop                           Café        Sandwich Place   
25        

In [31]:
Toronto_merged.loc[Toronto_merged['Cluster Labels'] == 4, Toronto_merged.columns[[2] + list(range(5, Toronto_merged.shape[1]))]]

Neighbourhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0   The Beaches               4     Health Food Store         Grocery Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Astrologer                   Pub         Women's Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0   Dumpling Restaurant        Discount Store               Dog Run   

  9th Most Common Venue 10th Most Common Venue  
0      Doner Restaurant             Donut Shop

For an additional evaluation, lets check how many bars or pubs there are in each neighborhood in Torronto.

In [32]:
Toronto_bar_venues = Toronto_venues[Toronto_venues['Venue Category'].str.contains('Pub|pub|bar|Bar|Speakeasy')].reset_index(drop=True)
print(Toronto_bar_venues.shape)
Toronto_bar_venues
#Remove any reccords where the bar does not have alcohol (e.g. juice bars, barbershops, hookah bars).
to_drop = ['Salon / Barbershop', 'Juice Bar', 'Hookah Bar']
Toronto_bar_and_pub_only_venues = Toronto_bar_venues[~Toronto_bar_venues['Venue Category'].isin(to_drop)]
Toronto_bar_and_pub_only_venues

(153, 7)


Neighborhood  Neighborhood Latitude  \
0                                          The Beaches              43.676357   
1                         The Danforth West, Riverdale              43.679557   
3                       The Beaches West, India Bazaar              43.668999   
4                                      Studio District              43.659526   
5                                      Studio District              43.659526   
6                                      Studio District              43.659526   
8    Deer Park, Forest Hill SE, Rathnelly, South Hi...              43.686412   
9    Deer Park, Forest Hill SE, Rathnelly, South Hi...              43.686412   
10   Deer Park, Forest Hill SE, Rathnelly, South Hi...              43.686412   
11                         Cabbagetown, St. James Town              43.667967   
12                         Cabbagetown, St. James Town              43.667967   
13                         Cabbagetown, St. James Town              43.667967   
15                                Church and Wellesley              43.665860   
17                                Church and Wellesley              43.665860   
18                                Church and Wellesley              43.665860   
19                                Church and Wellesley              43.665860   
20                                Church and Wellesley              43.665860   
21                                Church and Wellesley              43.665860   
22                                Church and Wellesley              43.665860   
23                                Church and Wellesley              43.665860   
24                                Church and Wellesley              43.665860   
25                           Harbourfront, Regent Park              43.654260   
26                           Harbourfront, Regent Park              43.654260   
27                           Harbourfront, Regent Park              43.654260   
28                            Ryerson, Garden District              43.657162   
29                            Ryerson, Garden District              43.657162   
31                            Ryerson, Garden District              43.657162   
33                            Ryerson, Garden District              43.657162   
34                            Ryerson, Garden District              43.657162   
35                                      St. James Town              43.651494   
36                                      St. James Town              43.651494   
37                                      St. James Town              43.651494   
38                                      St. James Town              43.651494   
39                                      St. James Town              43.651494   
40                                      St. James Town              43.651494   
41                                      St. James Town              43.651494   
42                                      St. James Town              43.651494   
43                                         Berczy Park              43.644771   
44                                         Berczy Park              43.644771   
45                                         Berczy Park              43.644771   
46                                         Berczy Park              43.644771   
47                                         Berczy Park              43.644771   
48                                         Berczy Park              43.644771   
49                                  Central Bay Street              43.657952   
50                                  Central Bay Street              43.657952   
51                                  Central Bay Street              43.657952   
53                                  Central Bay Street              43.657952   
54                            Adelaide, King, Richmond              43.650571   
55                            Adelaide, King, Richmond              43.65

Let's group by neighborhood and count how many pubs or bars are in each neighborhood, and remove excess columns.

In [37]:
Toronto_bar_and_pub_only_venues_count = Toronto_bar_and_pub_only_venues.groupby('Neighborhood').count()

del Toronto_bar_and_pub_only_venues_count['Neighborhood Latitude']
del Toronto_bar_and_pub_only_venues_count['Neighborhood Longitude']
del Toronto_bar_and_pub_only_venues_count['Venue']
del Toronto_bar_and_pub_only_venues_count['Venue Latitude']
del Toronto_bar_and_pub_only_venues_count['Venue Longitude']

Toronto_bar_and_pub_only_venues_count.rename(columns={'Venue Category':'Count of Bars and Pubs'}, inplace=True)

Toronto_bar_and_pub_only_venues_count.sort_values(by=('Count of Bars and Pubs'))

Count of Bars and Pubs
Neighborhood                                                              
The Danforth West, Riverdale                                             1
The Beaches West, India Bazaar                                           1
Dovercourt Village, Dufferin                                             1
The Annex, North Midtown, Yorkville                                      1
The Beaches                                                              1
Parkdale, Roncesvalles                                                   1
Brockton, Exhibition Place, Parkdale Village                             1
Cabbagetown, St. James Town                                              3
Studio District                                                          3
Runnymede, Swansea                                                       3
Harbourfront, Regent Park                                                3
Deer Park, Forest Hill SE, Rathnelly, South Hil...                       3
High Park, The Junction South                                            4
Harbord, University of Toronto                                           4
Central Bay Street                                                       4
Ryerson, Garden District                                                 5
Berczy Park                                                              6
Harbourfront East, Toronto Islands, Union Station                        7
St. James Town                                                           8
Adelaide, King, Richmond                                                 8
Stn A PO Boxes 25 The Esplanade                                          9
Church and Wellesley                                                     9
Chinatown, Grange Park, Kensington Market                                9
First Canadian Place, Underground city                                  11
Commerce Court, Victoria Hotel                                          11
Little Portugal, Trinity                                                12
Design Exchange, Toronto Dominion Centre                                13

Now let's evaluate New York, and then we can look at neighborhoods in New York as well as Toronto.

Download a dataset with information about New Yor Neighborhoods.   has a total of 5 boroughs and 306 neighborhoods. In order to segement the neighborhoods and explore them, we will essentially need a dataset that contains the 5 boroughs and the neighborhoods that exist in each borough as well as the the latitude and logitude coordinates of each neighborhood.

The dataset can be found at this link: https://geo.nyu.edu/catalog/nyu_2451_34572

The files are also available on a Coursera course server, so I can use a wget command to access the data. 

In [38]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


Load the New York data:

In [39]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

After viewing the json information, I see that all the relevant data is in the features key, which is basically a list of the neighborhoods. I'll define a new variable that includes this data, and then transform the information into a pandas dataframe.

In [40]:
neighborhoods_data = newyork_data['features']

# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

 Then I'll loop through the data and fill the dataframe one row at a time.

In [41]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

I'll use the geopy library to get the latitude and longitude values of New York City.
In order to define an instance of the geocoder, I'll define a user_agent (ny_explorer).

In [42]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


Now I'll reate a map of New York with neighborhoods superimposed on top.

In [43]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

I'll create a new dataframe that narrows the New York data to Manhattan, and visualize the neighborhoods on a map.

In [44]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)

map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

I'll create a function to identify the nearby venues of all of the neighborhoods in Manhattan.

In [45]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

I'll connect to the Foursquare API.

In [46]:
CLIENT_ID = '1YIGHKEQNF3RB4KKN0HFHIMEO2IGG5OD53WYTZACPOXKCQJZ' # your Foursquare ID
CLIENT_SECRET = 'JZKJHWBNLIHXZPGMC1NOFZKRMI3WCFVDLXIRVKNUUDT4PSMS' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 1YIGHKEQNF3RB4KKN0HFHIMEO2IGG5OD53WYTZACPOXKCQJZ
CLIENT_SECRET:JZKJHWBNLIHXZPGMC1NOFZKRMI3WCFVDLXIRVKNUUDT4PSMS


Now I'll set the limit of venues to return and the radius distance.  Then I'll get the neighborhood latitudes and longitudes, as well as the neighborhood names.  I will then refer to the url, and create a variable to store the results of the url json information.  I will also create a new dataframe called manhattan_venues.

In [47]:
LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 500 # define radius

neighborhood_latitude = manhattan_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = manhattan_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = manhattan_data.loc[0, 'Neighborhood'] # neighborhood name

url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)

results = requests.get(url).json()

In [49]:
manhattan_venues = getNearbyVenues(names=manhattan_data['Neighborhood'],
                                   latitudes=manhattan_data['Latitude'],
                                   longitudes=manhattan_data['Longitude']
                                  )

Marble Hill
Chinatown
Washington Heights
Inwood
Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper East Side
Yorkville
Lenox Hill
Roosevelt Island
Upper West Side
Lincoln Square
Clinton
Midtown
Murray Hill
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Little Italy
Soho
West Village
Manhattan Valley
Morningside Heights
Gramercy
Battery Park City
Financial District
Carnegie Hill
Noho
Civic Center
Midtown South
Sutton Place
Turtle Bay
Tudor City
Stuyvesant Town
Flatiron
Hudson Yards


I'll take a look at the venues for each Manhattan neighborhood.

In [50]:
print(manhattan_venues.shape)
manhattan_venues.head()

(3309, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude          Venue  \
0  Marble Hill              40.876551               -73.91066       Arturo's   
1  Marble Hill              40.876551               -73.91066    Bikram Yoga   
2  Marble Hill              40.876551               -73.91066  Tibbett Diner   
3  Marble Hill              40.876551               -73.91066        Dunkin'   
4  Marble Hill              40.876551               -73.91066      Starbucks   

   Venue Latitude  Venue Longitude Venue Category  
0       40.874412       -73.910271    Pizza Place  
1       40.876844       -73.906204    Yoga Studio  
2       40.880404       -73.908937          Diner  
3       40.877136       -73.906666     Donut Shop  
4       40.877531       -73.905582    Coffee Shop

Now, just as I did for Torronto, I'll count how many bars and pubs there are in each Manhattan neighborhood.

In [51]:
manhattan_bar_venues = manhattan_venues[manhattan_venues['Venue Category'].str.contains('Pub|pub|bar|Bar|Speakeasy')].reset_index(drop=True)
manhattan_bar_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Chinatown              40.715618              -73.994279   
1    Chinatown              40.715618              -73.994279   
2    Chinatown              40.715618              -73.994279   
3    Chinatown              40.715618              -73.994279   
4    Chinatown              40.715618              -73.994279   

                       Venue  Venue Latitude  Venue Longitude  \
0                  Bar Belly       40.715135       -73.991802   
1                       WOON       40.716081       -73.991681   
2             Boys Don't Cry       40.715396       -73.991623   
3               Rabbit House       40.717233       -73.993269   
4  Mian Tian Sing Hair Salon       40.716630       -73.997328   

       Venue Category  
0        Cocktail Bar  
1  Salon / Barbershop  
2                 Bar  
3            Sake Bar  
4  Salon / Barbershop

In [52]:
manhattan_bar_venues.shape

(273, 7)

In [53]:
#Remove any reccords where the bar does not have alcohol (e.g. juice bars, barbershops, hookah bars).
to_drop = ['Salon / Barbershop', 'Juice Bar', 'Hookah Bar']
manhattan_bar_and_pub_only_venues = manhattan_bar_venues[~manhattan_bar_venues['Venue Category'].isin(to_drop)]
manhattan_bar_and_pub_only_venues.shape

(226, 7)

In [201]:
manhattan_bar_and_pub_only_venues_count = manhattan_bar_and_pub_only_venues.groupby('Neighborhood').count()

del manhattan_bar_and_pub_only_venues_count['Neighborhood Latitude']
del manhattan_bar_and_pub_only_venues_count['Neighborhood Longitude']
del manhattan_bar_and_pub_only_venues_count['Venue']
del manhattan_bar_and_pub_only_venues_count['Venue Latitude']
del manhattan_bar_and_pub_only_venues_count['Venue Longitude']

manhattan_bar_and_pub_only_venues_count.rename(columns={'Venue Category':'Count of Bars and Pubs'}, inplace=True)

manhattan_bar_and_pub_only_venues_count.sort_values(by=('Count of Bars and Pubs'))

Count of Bars and Pubs
Neighborhood                               
Morningside Heights                       1
Manhattanville                            1
Flatiron                                  1
Lincoln Square                            2
East Harlem                               2
Soho                                      2
Battery Park City                         2
Inwood                                    3
Manhattan Valley                          3
Lower East Side                           3
Washington Heights                        3
Stuyvesant Town                           3
Midtown                                   4
Chelsea                                   4
Central Harlem                            4
Lenox Hill                                4
Upper East Side                           5
Little Italy                              5
Greenwich Village                         5
Hudson Yards                              5
Hamilton Heights                          6
Chinatown                                 6
Sutton Place                              6
Financial District                        7
Civic Center                              7
Carnegie Hill                             8
Tribeca                                   8
Yorkville                                 9
Turtle Bay                                9
Murray Hill                               9
Clinton                                  10
Noho                                     11
Midtown South                            12
Upper West Side                          12
Gramercy                                 13
West Village                             14
East Village                             16

In [55]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                      100                     100    100   
Carnegie Hill                          100                     100    100   
Central Harlem                          46                      46     46   
Chelsea                                100                     100    100   
Chinatown                              100                     100    100   
Civic Center                           100                     100    100   
Clinton                                100                     100    100   
East Harlem                             48                      48     48   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                               100                     100    100   
Gramercy                               100                     100    100   
Greenwich Village                      100                     100    100   
Hamilton Heights                        59                      59     59   
Hudson Yards                            76                      76     76   
Inwood                                  56                      56     56   
Lenox Hill                             100                     100    100   
Lincoln Square                         100                     100    100   
Little Italy                           100                     100    100   
Lower East Side                         58                      58     58   
Manhattan Valley                        59                      59     59   
Manhattanville                          39                      39     39   
Marble Hill                             24                      24     24   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Morningside Heights                     39                      39     39   
Murray Hill                            100                     100    100   
Noho                                   100                     100    100   
Roosevelt Island                        21                      21     21   
Soho                                   100                     100    100   
Stuyvesant Town                         18                      18     18   
Sutton Place                           100                     100    100   
Tribeca                                100                     100    100   
Tudor City                              81                      81     81   
Turtle Bay                             100                     100    100   
Upper East Side                        100                     100    100   
Upper West Side                        100                     100    100   
Washington Heights                      85                      85     85   
West Village                           100                     100    100   
Yorkville                              100                     100    100   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City               100              100             100  
Carnegie Hill                   100              100             100  
Central Harlem                   46               46              46  
Chelsea                         100              100             100  
Chinatown                       100              100             100  
Civic Center                    100              100             100  
Clinton                         100              100             100  
East Harlem                      48               48              48  
East Village                    100              100             100  
Finan

Now I'll analyze each neighborhood and perform one hot encoding.

In [56]:
# one hot encoding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  Marble Hill                  0               0                  0   
1  Marble Hill                  0               0                  0   
2  Marble Hill                  0               0                  0   
3  Marble Hill                  0               0                  0   
4  Marble Hill                  0               0                  0   

   African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0                   0                    0               0             0   
1                   0                    0               0             0   
2                   0                    0               0             0   
3                   0                    0               0             0   
4                   0                    0               0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                    0                 0                   0           0   
1                    0                 0                   0           0   
2                    0                 0                   0           0   
3                    0                 0                   0           0   
4                    0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  BBQ Joint  \
0                      0                    0              0          0   
1                      0                    0              0          0   
2                      0                    0              0          0   
3                      0                    0              0          0   
4                      0                    0              0          0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0           0           0       0     0    0               0   
1           0           0       0     0    0               0   
2           0           0       0     0    0               0   
3           0           0       0     0    0               0   
4           0           0       0     0    0               0   

   Basketball Court  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                 0         0            0           0              0   
1                 0         0            0           0              0   
2                 0         0            0           0              0   
3                 0         0            0           0              0   
4                 0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0              0          0         0           0                     0   
1              0          0         0           0                     0   
2              0          0         0           0                     0   
3              0          0         0           0                     0   
4              0          0         0           0                     0   

   

Next, I'll group rows by neighborhood take the mean of the frequency of occurrence of each category.

In [57]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Battery Park City           0.000000            0.00               0.00   
1         Carnegie Hill           0.000000            0.00               0.00   
2        Central Harlem           0.000000            0.00               0.00   
3               Chelsea           0.000000            0.00               0.00   
4             Chinatown           0.000000            0.00               0.00   
5          Civic Center           0.000000            0.00               0.00   
6               Clinton           0.000000            0.00               0.00   
7           East Harlem           0.000000            0.00               0.00   
8          East Village           0.000000            0.00               0.00   
9    Financial District           0.010000            0.00               0.00   
10             Flatiron           0.000000            0.00               0.00   
11             Gramercy           0.000000            0.00               0.00   
12    Greenwich Village           0.000000            0.00               0.00   
13     Hamilton Heights           0.000000            0.00               0.00   
14         Hudson Yards           0.000000            0.00               0.00   
15               Inwood           0.000000            0.00               0.00   
16           Lenox Hill           0.000000            0.00               0.01   
17       Lincoln Square           0.000000            0.00               0.00   
18         Little Italy           0.000000            0.00               0.00   
19      Lower East Side           0.000000            0.00               0.00   
20     Manhattan Valley           0.000000            0.00               0.00   
21       Manhattanville           0.000000            0.00               0.00   
22          Marble Hill           0.000000            0.00               0.00   
23              Midtown           0.000000            0.00               0.00   
24        Midtown South           0.000000            0.00               0.00   
25  Morningside Heights           0.000000            0.00               0.00   
26          Murray Hill           0.000000            0.00               0.00   
27                 Noho           0.000000            0.01               0.00   
28     Roosevelt Island           0.000000            0.00               0.00   
29                 Soho           0.010000            0.00               0.00   
30      Stuyvesant Town           0.000000            0.00               0.00   
31         Sutton Place           0.000000            0.01               0.00   
32              Tribeca           0.000000            0.00               0.00   
33           Tudor City           0.000000            0.00               0.00   
34           Turtle Bay           0.000000            0.00               0.00   
35      Upper East Side           0.000000            0.00               0.00   
36      Upper West Side           0.010000            0.00               0.00   
37   Washington Heights           0.011765            0.00               0.00   
38         West Village           0.010000            0.00               0.00   
39            Yorkville           0.000000            0.00               0.00   

    African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0             0.000000             0.010000            0.00          0.00   
1             0.000000             0.010000            0.00          0.00   
2             0.065217             0.043478            0.00          0.00   
3             0.000000             0.040000            0.00          0.01   
4             0.000000             0.040000            0.00          0.00   
5             0.000000             0.030000            0.00          0.01   
6             0.000000             0.040000            0.00          0.00   
7             0.000000             0.000000            0.00          0.00

I'll take a look at the top 5 venues in each neighborhood.

In [58]:
num_top_venues = 5

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
           venue  freq
0           Park  0.08
1    Coffee Shop  0.07
2          Hotel  0.05
3  Memorial Site  0.04
4      Wine Shop  0.03


----Carnegie Hill----
         venue  freq
0  Coffee Shop  0.06
1  Pizza Place  0.06
2         Café  0.04
3  Yoga Studio  0.03
4    Bookstore  0.03


----Central Harlem----
                  venue  freq
0    African Restaurant  0.07
1  Gym / Fitness Center  0.04
2     French Restaurant  0.04
3         Deli / Bodega  0.04
4        Cosmetics Shop  0.04


----Chelsea----
                 venue  freq
0          Coffee Shop  0.06
1       Ice Cream Shop  0.05
2   Italian Restaurant  0.05
3  American Restaurant  0.04
4            Nightclub  0.04


----Chinatown----
                 venue  freq
0   Chinese Restaurant  0.10
1  American Restaurant  0.04
2         Cocktail Bar  0.04
3      Bubble Tea Shop  0.03
4                  Spa  0.03


----Civic Center----
                  venue  freq
0    Italian Restaurant  0.06
1  Gym / Fit

Now I'll write a function to sort the venues in descending order, and create a dataframe that displays the top 10.

In [59]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [61]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City                  Park           Coffee Shop   
1      Carnegie Hill           Coffee Shop           Pizza Place   
2     Central Harlem    African Restaurant    Chinese Restaurant   
3            Chelsea           Coffee Shop        Ice Cream Shop   
4          Chinatown    Chinese Restaurant   American Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                 Hotel         Memorial Site        Clothing Store   
1                  Café           Yoga Studio   Japanese Restaurant   
2     French Restaurant        Cosmetics Shop   American Restaurant   
3    Italian Restaurant                Bakery             Nightclub   
4          Cocktail Bar   Dumpling Restaurant       Bubble Tea Shop   

  6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0             Wine Shop                    Gym    Italian Restaurant   
1             Bookstore                    Bar        Cosmetics Shop   
2         Deli / Bodega     Seafood Restaurant  Gym / Fitness Center   
3   American Restaurant     Seafood Restaurant                 Hotel   
4                   Spa  Vietnamese Restaurant    Salon / Barbershop   

  9th Most Common Venue  10th Most Common Venue  
0      Department Store               BBQ Joint  
1     French Restaurant                     Spa  
2            Public Art                 Library  
3               Theater            Cupcake Shop  
4     Hotpot Restaurant  Furniture / Home Store

In [62]:
neighborhoods_venues_sorted.shape

(40, 11)

In [63]:
manhattan_grouped.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  Battery Park City                0.0             0.0                0.0   
1      Carnegie Hill                0.0             0.0                0.0   
2     Central Harlem                0.0             0.0                0.0   
3            Chelsea                0.0             0.0                0.0   
4          Chinatown                0.0             0.0                0.0   

   African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0            0.000000             0.010000             0.0          0.00   
1            0.000000             0.010000             0.0          0.00   
2            0.065217             0.043478             0.0          0.00   
3            0.000000             0.040000             0.0          0.01   
4            0.000000             0.040000             0.0          0.00   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0     0.0               0.0                     0.0     0.000000        0.00   
1     0.0               0.0                     0.0     0.000000        0.01   
2     0.0               0.0                     0.0     0.021739        0.00   
3     0.0               0.0                     0.0     0.020000        0.00   
4     0.0               0.0                     0.0     0.000000        0.00   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                  0.0              0.00                0.01        0.01   
1                  0.0              0.00                0.00        0.00   
2                  0.0              0.00                0.00        0.00   
3                  0.0              0.01                0.00        0.00   
4                  0.0              0.02                0.00        0.00   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  BBQ Joint  \
0                    0.0                 0.00            0.0   0.020000   
1                    0.0                 0.00            0.0   0.000000   
2                    0.0                 0.00            0.0   0.021739   
3                    0.0                 0.00            0.0   0.000000   
4                    0.0                 0.01            0.0   0.000000   

   Baby Store  Bagel Shop  Bakery  Bank       Bar  Baseball Field  \
0         0.0    0.000000    0.01   0.0  0.000000             0.0   
1         0.0    0.010000    0.02   0.0  0.030000             0.0   
2         0.0    0.021739    0.00   0.0  0.021739             0.0   
3         0.0    0.000000    0.04   0.0  0.010000             0.0   
4         0.0    0.000000    0.02   0.0  0.010000             0.0   

   Basketball Court  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0               0.0  0.000000         0.01         0.0            0.0   
1               0.0  0.000000         0.00         0.0            0.0   
2               0.0  0.021739         0.00         0.0            0.0   
3               0.0  0.010000         0.00         0.0            0.0   
4               0.0  0.000000         0.00         0.0            0.0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                       0.0       0.00         0.0    0.01         0.0   
1                       0.0       0.00         0.0    0.00         0.0   
2                       0.0       0.00         0.0    0.00         0.0   
3                       0.0       0.00         0.0    0.00         0.0   
4                       0.0       0.01         0.0    0.00         0.0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0           0.01   0.000000  0.000000         0.0                   0.0   
1           0.00   0.030000  0.000000         0.0                   0.0   
2           0.00   0.021739  0.021739         0.0                   0.0   
3           0.00   0.020000  0.000000         0.0                   0.0   
4           0.00   

In [64]:
manhattan_grouped.shape

(40, 333)

Now I'll use k means to organize the neighborhoods into 5 clusters.

In [65]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 1, 0, 1, 0, 0, 1, 4, 1, 1], dtype=int32)

Now I'll create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [66]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               4   
1  Manhattan           Chinatown  40.715618 -73.994279               0   
2  Manhattan  Washington Heights  40.851903 -73.936900               4   
3  Manhattan              Inwood  40.867684 -73.921210               4   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Sandwich Place           Coffee Shop        Discount Store   
1    Chinese Restaurant   American Restaurant          Cocktail Bar   
2                  Café     Mobile Phone Shop                Bakery   
3                  Café    Mexican Restaurant                Lounge   
4                  Café           Pizza Place    Mexican Restaurant   

  4th Most Common Venue      5th Most Common Venue    6th Most Common Venue  \
0           Yoga Studio                      Diner               Steakhouse   
1   Dumpling Restaurant            Bubble Tea Shop                      Spa   
2       Supplement Shop  Latin American Restaurant  New American Restaurant   
3           Pizza Place                     Bakery       Frozen Yogurt Shop   
4           Coffee Shop                Yoga Studio         Sushi Restaurant   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Supplement Shop    Seafood Restaurant        Tennis Stadium   
1  Vietnamese Restaurant    Salon / Barbershop     Hotpot Restaurant   
2     Chinese Restaurant    Mexican Restaurant        Clothing Store   
3     Chinese Restaurant                  Park   American Restaurant   
4   Caribbean Restaurant    Chinese Restaurant                Bakery   

   10th Most Common Venue  
0                     Gym  
1  Furniture / Home Store  
2             Supermarket  
3           Deli / Bodega  
4                  School

Now I'll create a map to visualize the clusters.

In [67]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Now I'll take a look at each of the clusters.

In [68]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
1           Chinatown    Chinese Restaurant      American Restaurant   
6      Central Harlem    African Restaurant       Chinese Restaurant   
8     Upper East Side    Italian Restaurant                  Exhibit   
13     Lincoln Square               Theater     Gym / Fitness Center   
15            Midtown                 Hotel              Coffee Shop   
18  Greenwich Village    Italian Restaurant           Clothing Store   
21            Tribeca                   Spa                     Café   
22       Little Italy                Bakery           Clothing Store   
23               Soho        Clothing Store                 Boutique   
24       West Village    Italian Restaurant  New American Restaurant   
32       Civic Center    Italian Restaurant     Gym / Fitness Center   
35         Turtle Bay    Italian Restaurant                    Hotel   
38           Flatiron                   Gym              Yoga Studio   
39       Hudson Yards   American Restaurant       Italian Restaurant   

   3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
1           Cocktail Bar   Dumpling Restaurant           Bubble Tea Shop   
6      French Restaurant        Cosmetics Shop       American Restaurant   
8            Coffee Shop                Bakery      Gym / Fitness Center   
13          Concert Hall                  Café                     Plaza   
15               Theater          Cocktail Bar            Clothing Store   
18      Sushi Restaurant     French Restaurant                      Café   
21    Italian Restaurant              Boutique       American Restaurant   
22        Sandwich Place    Salon / Barbershop  Mediterranean Restaurant   
23            Shoe Store         Women's Store               Men's Store   
24        Cosmetics Shop             Jazz Club                      Park   
32                Bakery           Coffee Shop         French Restaurant   
35      Sushi Restaurant            Steakhouse               Coffee Shop   
38  Gym / Fitness Center   American Restaurant       Japanese Restaurant   
39           Coffee Shop                  Café                   Theater   

   6th Most Common Venue  7th Most Common Venue    8th Most Common Venue  \
1                    Spa  Vietnamese Restaurant       Salon / Barbershop   
6          Deli / Bodega     Seafood Restaurant     Gym / Fitness Center   
8            Art Gallery              Juice Bar                    Hotel   
13    Italian Restaurant            Opera House    Performing Arts Venue   
15   Sporting Goods Shop    American Restaurant      Japanese Restaurant   
18    Seafood Restaurant      Indian Restaurant           Ice Cream Shop   
21                  Park                    Gym                 Wine Bar   
22    Italian Restaurant     Seafood Restaurant                    Hotel   
23   Sporting Goods Shop            Art Gallery                   Bakery   
24              Wine Bar    American Restaurant                   Bakery   
32        Sandwich Place            Yoga Studio             Cocktail Bar   
35              Wine Bar                   Park        French Restaurant   
38                  Café         Clothing Store  New American Restaurant   
39  Gym / Fitness Center                  Hotel           Ice Cream Shop   

   9th Most Common Venue    10th Most Common Venue  
1      Hotpot Restaurant    Furniture / Home Store  
6             Public Art                   Library  
8                    Spa              Cocktail Bar  
13     French Restaurant                      Park  
15            Food Truck                       Spa  
18           Coffee Shop                       Spa  
21             Wine Shop          Greek Restaurant  
22                  Café              Cocktail Bar  
23    Italian Restaurant  Mediterranean Restaurant  
24           Coffee Shop                 Gastropub  
32                  Park       Sporting Goods Shop  
35   Japan

In [69]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
9            Yorkville    Italian Restaurant           Coffee Shop   
10          Lenox Hill           Coffee Shop    Italian Restaurant   
12     Upper West Side    Italian Restaurant              Wine Bar   
14             Clinton               Theater  Gym / Fitness Center   
16         Murray Hill                 Hotel        Sandwich Place   
17             Chelsea           Coffee Shop        Ice Cream Shop   
19        East Village                   Bar              Wine Bar   
25    Manhattan Valley     Indian Restaurant           Coffee Shop   
27            Gramercy   American Restaurant    Italian Restaurant   
29  Financial District           Coffee Shop            Steakhouse   
30       Carnegie Hill           Coffee Shop           Pizza Place   
31                Noho    Italian Restaurant     French Restaurant   
33       Midtown South     Korean Restaurant                 Hotel   
34        Sutton Place    Italian Restaurant  Gym / Fitness Center   

   3rd Most Common Venue   4th Most Common Venue     5th Most Common Venue  \
9                    Gym                     Bar               Pizza Place   
10      Sushi Restaurant             Pizza Place       Sporting Goods Shop   
12                   Bar             Coffee Shop  Mediterranean Restaurant   
14   American Restaurant      Italian Restaurant                     Hotel   
16   Japanese Restaurant             Coffee Shop        Italian Restaurant   
17    Italian Restaurant                  Bakery                 Nightclub   
19        Ice Cream Shop      Mexican Restaurant        Chinese Restaurant   
25           Pizza Place             Yoga Studio                       Bar   
27            Bagel Shop                     Bar               Pizza Place   
29                   Gym               Wine Shop                     Hotel   
30                  Café             Yoga Studio       Japanese Restaurant   
31          Cocktail Bar      Mexican Restaurant                  Boutique   
33             Hotel Bar             Coffee Shop       Japanese Restaurant   
34     Indian Restaurant  Furniture / Home Store       American Restaurant   

   6th Most Common Venue 7th Most Common Venue          8th Most Common Venue  \
9       Sushi Restaurant        Ice Cream Shop            Japanese Restaurant   
10          Burger Joint                   Gym           Gym / Fitness Center   
12                Bakery     Indian Restaurant  Vegetarian / Vegan Restaurant   
14             Wine Shop           Coffee Shop                            Spa   
16    Salon / Barbershop     French Restaurant                            Gym   
17   American Restaurant    Seafood Restaurant                          Hotel   
19          Cocktail Bar           Pizza Place               Ramen Restaurant   
25   Szechuan Restaurant       Thai Restaurant             Mexican Restaurant   
27          Cocktail Bar         Grocery Store                          Hotel   
29                  Park           Pizza Place                            Bar   
30             Bookstore                   Bar                 Cosmetics Shop   
31           Art Gallery             Rock Club                    Coffee Shop   
33  Gym / Fitness Center        Cosmetics Shop            American Restaurant   
34           Pizza Place             Juice Bar                            Gym   

   9th Most Common Venue         10th Most Common Venue  
9              Wine Shop                  Deli / Bodega  
10        Cosmetics Shop                         Bakery  
12           Yoga Studio                            Pub  
14        Sandwich Place                    Pizza Place  
16                   Pub                     Taco Place  
17               Theater                   Cupcake Shop  
19           Coffee Shop  Vegetarian / Vegan Restaurant  
25                  Café                  Deli / Bodega  
27    Mexican Restaurant                Thai Resta

In [70]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
37  Stuyvesant Town                   Bar                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
37            Playground              Fountain     German Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
37        Baseball Field       Harbor / Marina          Cocktail Bar   

   9th Most Common Venue 10th Most Common Venue  
37           Coffee Shop         Farmers Market

In [71]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
11     Roosevelt Island           Coffee Shop                  Park   
26  Morningside Heights             Bookstore   American Restaurant   
28    Battery Park City                  Park           Coffee Shop   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
11        Sandwich Place   Rental Car Location              Bus Stop   
26           Coffee Shop                  Park         Deli / Bodega   
28                 Hotel         Memorial Site        Clothing Store   

   6th Most Common Venue 7th Most Common Venue  8th Most Common Venue  \
11           Supermarket        Farmers Market  Outdoors & Recreation   
26          Tennis Court          Burger Joint             Food Truck   
28             Wine Shop                   Gym     Italian Restaurant   

   9th Most Common Venue 10th Most Common Venue  
11      Greek Restaurant           Liquor Store  
26     Outdoor Sculpture     Seafood Restaurant  
28      Department Store              BBQ Joint

In [72]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Marble Hill        Sandwich Place           Coffee Shop   
2   Washington Heights                  Café     Mobile Phone Shop   
3               Inwood                  Café    Mexican Restaurant   
4     Hamilton Heights                  Café           Pizza Place   
5       Manhattanville                  Park    Mexican Restaurant   
7          East Harlem         Deli / Bodega    Mexican Restaurant   
20     Lower East Side      Ramen Restaurant           Coffee Shop   
36          Tudor City                  Park    Mexican Restaurant   

   3rd Most Common Venue 4th Most Common Venue      5th Most Common Venue  \
0         Discount Store           Yoga Studio                      Diner   
2                 Bakery       Supplement Shop  Latin American Restaurant   
3                 Lounge           Pizza Place                     Bakery   
4     Mexican Restaurant           Coffee Shop                Yoga Studio   
5            Coffee Shop    Italian Restaurant         Seafood Restaurant   
7                 Bakery           Coffee Shop                        Spa   
20                  Café           Pizza Place         Chinese Restaurant   
36      Greek Restaurant                  Café           Asian Restaurant   

      6th Most Common Venue      7th Most Common Venue 8th Most Common Venue  \
0                Steakhouse            Supplement Shop    Seafood Restaurant   
2   New American Restaurant         Chinese Restaurant    Mexican Restaurant   
3        Frozen Yogurt Shop         Chinese Restaurant                  Park   
4          Sushi Restaurant       Caribbean Restaurant    Chinese Restaurant   
5          Cuban Restaurant               Music School                Lounge   
7           Thai Restaurant  Latin American Restaurant        Sandwich Place   
20              Art Gallery                     Bakery   Japanese Restaurant   
36            Deli / Bodega                Pizza Place                 Hotel   

   9th Most Common Venue 10th Most Common Venue  
0         Tennis Stadium                    Gym  
2         Clothing Store            Supermarket  
3    American Restaurant          Deli / Bodega  
4                 Bakery                 School  
5             Bike Trail       Sushi Restaurant  
7                   Bank               Beer Bar  
20          Cocktail Bar         Sandwich Place  
36               Dog Run     Spanish Restaurant

Okay, now that I have reviewed the neighborhoods in Toronto and Manhattan separately, I will combine them into one dataset and perform a new round of k means clustering, to determine which neighborhoods in Toronto are similar to neighborhoods in Manhattan.

I'll join the two dataframes (Toronto and Manhattan) containing the neighborhoods and the top 10 venues, sorted in descending order.

Let's look at each dataframe again that we used for generating k means clustering analysis, starting with Manhattan.

In [73]:
manhattan_grouped.head() #Manhattan dataframe

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  Battery Park City                0.0             0.0                0.0   
1      Carnegie Hill                0.0             0.0                0.0   
2     Central Harlem                0.0             0.0                0.0   
3            Chelsea                0.0             0.0                0.0   
4          Chinatown                0.0             0.0                0.0   

   African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0            0.000000             0.010000             0.0          0.00   
1            0.000000             0.010000             0.0          0.00   
2            0.065217             0.043478             0.0          0.00   
3            0.000000             0.040000             0.0          0.01   
4            0.000000             0.040000             0.0          0.00   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0     0.0               0.0                     0.0     0.000000        0.00   
1     0.0               0.0                     0.0     0.000000        0.01   
2     0.0               0.0                     0.0     0.021739        0.00   
3     0.0               0.0                     0.0     0.020000        0.00   
4     0.0               0.0                     0.0     0.000000        0.00   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                  0.0              0.00                0.01        0.01   
1                  0.0              0.00                0.00        0.00   
2                  0.0              0.00                0.00        0.00   
3                  0.0              0.01                0.00        0.00   
4                  0.0              0.02                0.00        0.00   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  BBQ Joint  \
0                    0.0                 0.00            0.0   0.020000   
1                    0.0                 0.00            0.0   0.000000   
2                    0.0                 0.00            0.0   0.021739   
3                    0.0                 0.00            0.0   0.000000   
4                    0.0                 0.01            0.0   0.000000   

   Baby Store  Bagel Shop  Bakery  Bank       Bar  Baseball Field  \
0         0.0    0.000000    0.01   0.0  0.000000             0.0   
1         0.0    0.010000    0.02   0.0  0.030000             0.0   
2         0.0    0.021739    0.00   0.0  0.021739             0.0   
3         0.0    0.000000    0.04   0.0  0.010000             0.0   
4         0.0    0.000000    0.02   0.0  0.010000             0.0   

   Basketball Court  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0               0.0  0.000000         0.01         0.0            0.0   
1               0.0  0.000000         0.00         0.0            0.0   
2               0.0  0.021739         0.00         0.0            0.0   
3               0.0  0.010000         0.00         0.0            0.0   
4               0.0  0.000000         0.00         0.0            0.0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                       0.0       0.00         0.0    0.01         0.0   
1                       0.0       0.00         0.0    0.00         0.0   
2                       0.0       0.00         0.0    0.00         0.0   
3                       0.0       0.00         0.0    0.00         0.0   
4                       0.0       0.01         0.0    0.00         0.0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0           0.01   0.000000  0.000000         0.0                   0.0   
1           0.00   0.030000  0.000000         0.0                   0.0   
2           0.00   0.021739  0.021739         0.0                   0.0   
3           0.00   0.020000  0.000000         0.0                   0.0   
4           0.00   

In [74]:
manhattan_grouped.shape

(40, 333)

In [72]:
Toronto_grouped.head() #Toronto dataframe

Neighborhood  Yoga Studio  \
0                           Adelaide, King, Richmond          0.0   
1                                        Berczy Park          0.0   
2       Brockton, Exhibition Place, Parkdale Village          0.0   
3  Business Reply Mail Processing Centre 969 Eastern          0.0   
4  CN Tower, Bathurst Quay, Island airport, Harbo...          0.0   

   Adult Boutique  Afghan Restaurant   Airport  Airport Food Court  \
0             0.0                0.0  0.000000            0.000000   
1             0.0                0.0  0.000000            0.000000   
2             0.0                0.0  0.000000            0.000000   
3             0.0                0.0  0.000000            0.000000   
4             0.0                0.0  0.071429            0.071429   

   Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0      0.000000        0.000000         0.000000          0.000000   
1      0.000000        0.000000         0.000000          0.000000   
2      0.000000        0.000000         0.000000          0.000000   
3      0.000000        0.000000         0.000000          0.000000   
4      0.071429        0.142857         0.214286          0.142857   

   American Restaurant  Antique Shop  Aquarium  Art Gallery  Art Museum  \
0                 0.04           0.0       0.0     0.010000        0.01   
1                 0.00           0.0       0.0     0.017857        0.00   
2                 0.00           0.0       0.0     0.000000        0.00   
3                 0.00           0.0       0.0     0.000000        0.00   
4                 0.00           0.0       0.0     0.000000        0.00   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Workshop  \
0                  0.0              0.02                 0.0         0.0000   
1                  0.0              0.00                 0.0         0.0000   
2                  0.0              0.00                 0.0         0.0000   
3                  0.0              0.00                 0.0         0.0625   
4                  0.0              0.00                 0.0         0.0000   

   BBQ Joint  Baby Store  Bagel Shop    Bakery  Bank       Bar  \
0        0.0         0.0    0.000000  0.030000   0.0  0.040000   
1        0.0         0.0    0.017857  0.035714   0.0  0.000000   
2        0.0         0.0    0.000000  0.000000   0.0  0.052632   
3        0.0         0.0    0.000000  0.000000   0.0  0.000000   
4        0.0         0.0    0.000000  0.000000   0.0  0.000000   

   Baseball Stadium  Basketball Stadium     Beach  Bed & Breakfast  Beer Bar  \
0               0.0            0.000000  0.000000              0.0  0.000000   
1               0.0            0.017857  0.017857              0.0  0.035714   
2               0.0            0.000000  0.000000              0.0  0.000000   
3               0.0            0.000000  0.000000              0.0  0.000000   
4               0.0            0.000000  0.000000              0.0  0.000000   

   Beer Store  Belgian Restaurant    Bistro  Boat or Ferry  Bookstore  \
0         0.0            0.000000  0.000000       0.000000       0.01   
1         0.0            0.017857  0.017857       0.000000       0.00   
2         0.0            0.000000  0.000000       0.000000       0.00   
3         0.0            0.000000  0.000000       0.000000       0.00   
4         0.0            0.000000  0.000000       0.071429       0.00   

   Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  \
0  0.000000                  0.01        0.020000   0.0000              0.0   
1  0.000000                  0.00        0.017857   0.0000              0.0   
2  0.000000                  0.00        0.105263   0.0000              0.0   
3  0.000000                  0.00        0.000000   0.0625              0.0   
4  0.071429                  0.00        0.000000   0.0000              0.0   

   Burger Joint  Burrito Place  Bus Line  Bus Stop  Butcher      

In [75]:
Toronto_grouped.shape

(38, 235)

In [76]:
combined_toronto_and_manhattan_neighborhoods = manhattan_grouped.append([Toronto_grouped], ignore_index=False, verify_integrity=False)
combined_toronto_and_manhattan_neighborhoods

Accessories Store  Adult Boutique  Afghan Restaurant  African Restaurant  \
0            0.000000        0.000000           0.000000            0.000000   
1            0.000000        0.000000           0.000000            0.000000   
2            0.000000        0.000000           0.000000            0.065217   
3            0.000000        0.000000           0.000000            0.000000   
4            0.000000        0.000000           0.000000            0.000000   
5            0.000000        0.000000           0.000000            0.000000   
6            0.000000        0.000000           0.000000            0.000000   
7            0.000000        0.000000           0.000000            0.000000   
8            0.000000        0.000000           0.000000            0.000000   
9            0.010000        0.000000           0.000000            0.000000   
10           0.000000        0.000000           0.000000            0.000000   
11           0.000000        0.000000           0.000000            0.000000   
12           0.000000        0.000000           0.000000            0.000000   
13           0.000000        0.000000           0.000000            0.000000   
14           0.000000        0.000000           0.000000            0.000000   
15           0.000000        0.000000           0.000000            0.000000   
16           0.000000        0.000000           0.010000            0.000000   
17           0.000000        0.000000           0.000000            0.000000   
18           0.000000        0.000000           0.000000            0.000000   
19           0.000000        0.000000           0.000000            0.000000   
20           0.000000        0.000000           0.000000            0.000000   
21           0.000000        0.000000           0.000000            0.000000   
22           0.000000        0.000000           0.000000            0.000000   
23           0.000000        0.000000           0.000000            0.000000   
24           0.000000        0.000000           0.000000            0.000000   
25           0.000000        0.000000           0.000000            0.000000   
26           0.000000        0.000000           0.000000            0.000000   
27           0.000000        0.010000           0.000000            0.000000   
28           0.000000        0.000000           0.000000            0.000000   
29           0.010000        0.000000           0.000000            0.000000   
30           0.000000        0.000000           0.000000            0.000000   
31           0.000000        0.010000           0.000000            0.000000   
32           0.000000        0.000000           0.000000            0.000000   
33           0.000000        0.000000           0.000000            0.000000   
34           0.000000        0.000000           0.000000            0.000000   
35           0.000000        0.000000           0.000000            0.000000   
36           0.010000        0.000000           0.000000            0.000000   
37           0.011765        0.000000           0.000000            0.000000   
38           0.010000        0.000000           0.000000            0.000000   
39           0.000000        0.000000           0.000000            0.000000   
0                 NaN        0.000000           0.000000                 NaN   
1                 NaN        0.000000           0.000000                 NaN   
2                 NaN        0.000000           0.000000                 NaN   
3                 NaN        0.000000           0.000000                 NaN   
4                 NaN        0.000000           0.000000                 NaN   
5                 NaN        0.000000           0.000000                 NaN   
6                 NaN        0.000000           0.000000                 NaN   
7                 NaN        0.000000           0.000000                 NaN   
8                 NaN        0.000000           0.000000                 NaN   
9   

In [77]:
combined_toronto_and_manhattan_neighborhoods.shape

(78, 379)

In [78]:
combined_toronto_and_manhattan_neighborhoods = combined_toronto_and_manhattan_neighborhoods.reset_index(drop=True)

In [77]:
combined_toronto_and_manhattan_neighborhoods

Accessories Store  Adult Boutique  Afghan Restaurant  African Restaurant  \
0            0.000000        0.000000           0.000000            0.000000   
1            0.000000        0.000000           0.000000            0.000000   
2            0.000000        0.000000           0.000000            0.069767   
3            0.000000        0.000000           0.000000            0.000000   
4            0.000000        0.000000           0.000000            0.000000   
5            0.000000        0.000000           0.000000            0.000000   
6            0.000000        0.000000           0.000000            0.000000   
7            0.000000        0.000000           0.000000            0.000000   
8            0.000000        0.000000           0.000000            0.000000   
9            0.010000        0.000000           0.000000            0.000000   
10           0.000000        0.000000           0.000000            0.000000   
11           0.000000        0.000000           0.000000            0.000000   
12           0.000000        0.000000           0.000000            0.000000   
13           0.000000        0.000000           0.000000            0.000000   
14           0.000000        0.000000           0.000000            0.000000   
15           0.000000        0.000000           0.000000            0.000000   
16           0.000000        0.000000           0.010000            0.000000   
17           0.000000        0.000000           0.000000            0.000000   
18           0.000000        0.000000           0.000000            0.000000   
19           0.000000        0.000000           0.000000            0.000000   
20           0.000000        0.000000           0.000000            0.000000   
21           0.000000        0.000000           0.000000            0.000000   
22           0.000000        0.000000           0.000000            0.000000   
23           0.000000        0.000000           0.000000            0.000000   
24           0.000000        0.000000           0.000000            0.000000   
25           0.000000        0.000000           0.000000            0.000000   
26           0.000000        0.000000           0.000000            0.000000   
27           0.000000        0.010000           0.000000            0.000000   
28           0.000000        0.000000           0.000000            0.000000   
29           0.000000        0.000000           0.000000            0.000000   
30           0.000000        0.000000           0.000000            0.000000   
31           0.000000        0.010000           0.000000            0.000000   
32           0.000000        0.000000           0.000000            0.000000   
33           0.000000        0.000000           0.000000            0.000000   
34           0.000000        0.000000           0.000000            0.000000   
35           0.000000        0.000000           0.000000            0.000000   
36           0.010000        0.000000           0.000000            0.000000   
37           0.011494        0.000000           0.000000            0.000000   
38           0.010000        0.000000           0.000000            0.000000   
39           0.000000        0.000000           0.000000            0.000000   
40                NaN        0.000000           0.000000                 NaN   
41                NaN        0.000000           0.000000                 NaN   
42                NaN        0.000000           0.000000                 NaN   
43                NaN        0.000000           0.000000                 NaN   
44                NaN        0.000000           0.000000                 NaN   
45                NaN        0.000000           0.000000                 NaN   
46                NaN        0.000000           0.000000                 NaN   
47                NaN        0.000000           0.000000                 NaN   
48                NaN        0.000000           0.000000                 NaN   
49  

Update the NaN results to 0

In [80]:
combined_toronto_and_manhattan_neighborhoods_filled = combined_toronto_and_manhattan_neighborhoods.fillna(0)
combined_toronto_and_manhattan_neighborhoods_filled

Accessories Store  Adult Boutique  Afghan Restaurant  African Restaurant  \
0            0.000000        0.000000           0.000000            0.000000   
1            0.000000        0.000000           0.000000            0.000000   
2            0.000000        0.000000           0.000000            0.065217   
3            0.000000        0.000000           0.000000            0.000000   
4            0.000000        0.000000           0.000000            0.000000   
5            0.000000        0.000000           0.000000            0.000000   
6            0.000000        0.000000           0.000000            0.000000   
7            0.000000        0.000000           0.000000            0.000000   
8            0.000000        0.000000           0.000000            0.000000   
9            0.010000        0.000000           0.000000            0.000000   
10           0.000000        0.000000           0.000000            0.000000   
11           0.000000        0.000000           0.000000            0.000000   
12           0.000000        0.000000           0.000000            0.000000   
13           0.000000        0.000000           0.000000            0.000000   
14           0.000000        0.000000           0.000000            0.000000   
15           0.000000        0.000000           0.000000            0.000000   
16           0.000000        0.000000           0.010000            0.000000   
17           0.000000        0.000000           0.000000            0.000000   
18           0.000000        0.000000           0.000000            0.000000   
19           0.000000        0.000000           0.000000            0.000000   
20           0.000000        0.000000           0.000000            0.000000   
21           0.000000        0.000000           0.000000            0.000000   
22           0.000000        0.000000           0.000000            0.000000   
23           0.000000        0.000000           0.000000            0.000000   
24           0.000000        0.000000           0.000000            0.000000   
25           0.000000        0.000000           0.000000            0.000000   
26           0.000000        0.000000           0.000000            0.000000   
27           0.000000        0.010000           0.000000            0.000000   
28           0.000000        0.000000           0.000000            0.000000   
29           0.010000        0.000000           0.000000            0.000000   
30           0.000000        0.000000           0.000000            0.000000   
31           0.000000        0.010000           0.000000            0.000000   
32           0.000000        0.000000           0.000000            0.000000   
33           0.000000        0.000000           0.000000            0.000000   
34           0.000000        0.000000           0.000000            0.000000   
35           0.000000        0.000000           0.000000            0.000000   
36           0.010000        0.000000           0.000000            0.000000   
37           0.011765        0.000000           0.000000            0.000000   
38           0.010000        0.000000           0.000000            0.000000   
39           0.000000        0.000000           0.000000            0.000000   
40           0.000000        0.000000           0.000000            0.000000   
41           0.000000        0.000000           0.000000            0.000000   
42           0.000000        0.000000           0.000000            0.000000   
43           0.000000        0.000000           0.000000            0.000000   
44           0.000000        0.000000           0.000000            0.000000   
45           0.000000        0.000000           0.000000            0.000000   
46           0.000000        0.000000           0.000000            0.000000   
47           0.000000        0.000000           0.000000            0.000000   
48           0.000000        0.000000           0.000000            0.000000   
49  

Now I'll perform cluster analysis on the combined data frame.

In [81]:
# set number of clusters
kclusters = 5

combined_toronto_and_manhattan_neighborhoods_clustering = combined_toronto_and_manhattan_neighborhoods_filled.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(combined_toronto_and_manhattan_neighborhoods_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

Now I'll combine the Toronto and Manhattan dataframes containing the top 10 venues for each neighborhood, sorted in descending order.

In [82]:
combined_sorted_venues = neighborhoods_venues_sorted.append([tneighborhoods_venues_sorted], ignore_index=False, verify_integrity=False)
combined_sorted_venues

Cluster Labels                                       Neighborhood  \
0                3                                  Battery Park City   
1                1                                      Carnegie Hill   
2                0                                     Central Harlem   
3                1                                            Chelsea   
4                0                                          Chinatown   
5                0                                       Civic Center   
6                1                                            Clinton   
7                4                                        East Harlem   
8                1                                       East Village   
9                1                                 Financial District   
10               0                                           Flatiron   
11               1                                           Gramercy   
12               0                                  Greenwich Village   
13               4                                   Hamilton Heights   
14               0                                       Hudson Yards   
15               4                                             Inwood   
16               1                                         Lenox Hill   
17               0                                     Lincoln Square   
18               0                                       Little Italy   
19               4                                    Lower East Side   
20               1                                   Manhattan Valley   
21               4                                     Manhattanville   
22               4                                        Marble Hill   
23               0                                            Midtown   
24               1                                      Midtown South   
25               3                                Morningside Heights   
26               1                                        Murray Hill   
27               1                                               Noho   
28               3                                   Roosevelt Island   
29               0                                               Soho   
30               2                                    Stuyvesant Town   
31               1                                       Sutton Place   
32               0                                            Tribeca   
33               4                                         Tudor City   
34               0                                         Turtle Bay   
35               0                                    Upper East Side   
36               1                                    Upper West Side   
37               4                                 Washington Heights   
38               0                                       West Village   
39               1                                          Yorkville   
0                3                           Adelaide, King, Richmond   
1                3                                        Berczy Park   
2                3       Brockton, Exhibition Place, Parkdale Village   
3                3  Business Reply Mail Processing Centre 969 Eastern   
4                3  CN Tower, Bathurst Quay, Island airport, Harbo...   
5                3                        Cabbagetown, St. James Town   
6                3                                 Central Bay Street   
7                3          Chinatown, Grange Park, Kensington Market   
8                3                                           Christie   
9                3                               Church and Wellesley   
10               3                     Commerce Court, Victoria Hotel   
11               3                                         Davisville   
12               3                                   Davisville North   
13               3  Deer Park, Forest Hill SE, Rathnelly, Sout

In [83]:
combined_sorted_venues = combined_sorted_venues.reset_index(drop=True)
combined_sorted_venues

Cluster Labels                                       Neighborhood  \
0                3                                  Battery Park City   
1                1                                      Carnegie Hill   
2                0                                     Central Harlem   
3                1                                            Chelsea   
4                0                                          Chinatown   
5                0                                       Civic Center   
6                1                                            Clinton   
7                4                                        East Harlem   
8                1                                       East Village   
9                1                                 Financial District   
10               0                                           Flatiron   
11               1                                           Gramercy   
12               0                                  Greenwich Village   
13               4                                   Hamilton Heights   
14               0                                       Hudson Yards   
15               4                                             Inwood   
16               1                                         Lenox Hill   
17               0                                     Lincoln Square   
18               0                                       Little Italy   
19               4                                    Lower East Side   
20               1                                   Manhattan Valley   
21               4                                     Manhattanville   
22               4                                        Marble Hill   
23               0                                            Midtown   
24               1                                      Midtown South   
25               3                                Morningside Heights   
26               1                                        Murray Hill   
27               1                                               Noho   
28               3                                   Roosevelt Island   
29               0                                               Soho   
30               2                                    Stuyvesant Town   
31               1                                       Sutton Place   
32               0                                            Tribeca   
33               4                                         Tudor City   
34               0                                         Turtle Bay   
35               0                                    Upper East Side   
36               1                                    Upper West Side   
37               4                                 Washington Heights   
38               0                                       West Village   
39               1                                          Yorkville   
40               3                           Adelaide, King, Richmond   
41               3                                        Berczy Park   
42               3       Brockton, Exhibition Place, Parkdale Village   
43               3  Business Reply Mail Processing Centre 969 Eastern   
44               3  CN Tower, Bathurst Quay, Island airport, Harbo...   
45               3                        Cabbagetown, St. James Town   
46               3                                 Central Bay Street   
47               3          Chinatown, Grange Park, Kensington Market   
48               3                                           Christie   
49               3                               Church and Wellesley   
50               3                     Commerce Court, Victoria Hotel   
51               3                                         Davisville   
52               3                                   Davisville North   
53               3  Deer Park, Forest Hill SE, Rathnelly, Sout

Now I'll create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [84]:
# add clustering labels
combined_sorted_venues.insert(0, 'Cluster Labels', kmeans.labels_)

ValueError: cannot insert Cluster Labels, already exists

In [85]:
combined_sorted_venues

Cluster Labels                                       Neighborhood  \
0                3                                  Battery Park City   
1                1                                      Carnegie Hill   
2                0                                     Central Harlem   
3                1                                            Chelsea   
4                0                                          Chinatown   
5                0                                       Civic Center   
6                1                                            Clinton   
7                4                                        East Harlem   
8                1                                       East Village   
9                1                                 Financial District   
10               0                                           Flatiron   
11               1                                           Gramercy   
12               0                                  Greenwich Village   
13               4                                   Hamilton Heights   
14               0                                       Hudson Yards   
15               4                                             Inwood   
16               1                                         Lenox Hill   
17               0                                     Lincoln Square   
18               0                                       Little Italy   
19               4                                    Lower East Side   
20               1                                   Manhattan Valley   
21               4                                     Manhattanville   
22               4                                        Marble Hill   
23               0                                            Midtown   
24               1                                      Midtown South   
25               3                                Morningside Heights   
26               1                                        Murray Hill   
27               1                                               Noho   
28               3                                   Roosevelt Island   
29               0                                               Soho   
30               2                                    Stuyvesant Town   
31               1                                       Sutton Place   
32               0                                            Tribeca   
33               4                                         Tudor City   
34               0                                         Turtle Bay   
35               0                                    Upper East Side   
36               1                                    Upper West Side   
37               4                                 Washington Heights   
38               0                                       West Village   
39               1                                          Yorkville   
40               3                           Adelaide, King, Richmond   
41               3                                        Berczy Park   
42               3       Brockton, Exhibition Place, Parkdale Village   
43               3  Business Reply Mail Processing Centre 969 Eastern   
44               3  CN Tower, Bathurst Quay, Island airport, Harbo...   
45               3                        Cabbagetown, St. James Town   
46               3                                 Central Bay Street   
47               3          Chinatown, Grange Park, Kensington Market   
48               3                                           Christie   
49               3                               Church and Wellesley   
50               3                     Commerce Court, Victoria Hotel   
51               3                                         Davisville   
52               3                                   Davisville North   
53               3  Deer Park, Forest Hill SE, Rathnelly, Sout

Join the two dataframes containing Toronto and Manhattan location data, so that I can add them to the dataframe with the cluster labels.

In [86]:
Torontodf.rename(columns={'Neighbourhood':'Neighborhood'}, inplace=True)  #first rename the column so that it is called Neighborhood in both dataframes.
Torontodf.head()

PostalCode          Borough                    Neighborhood   Latitude  \
0        M4E     East Toronto                     The Beaches  43.676357   
1        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
2        M4L     East Toronto  The Beaches West, India Bazaar  43.668999   
3        M4M     East Toronto                 Studio District  43.659526   
4        M4N  Central Toronto                   Lawrence Park  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [87]:
Torontodf.shape

(38, 5)

In [88]:
Torontodf_new = Torontodf.drop(['PostalCode'], axis=1)
Torontodf_new.head()

Borough                    Neighborhood   Latitude  Longitude
0     East Toronto                     The Beaches  43.676357 -79.293031
1     East Toronto    The Danforth West, Riverdale  43.679557 -79.352188
2     East Toronto  The Beaches West, India Bazaar  43.668999 -79.315572
3     East Toronto                 Studio District  43.659526 -79.340923
4  Central Toronto                   Lawrence Park  43.728020 -79.388790

In [89]:
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

In [90]:
combined_location_dataframe = Torontodf_new.append([manhattan_data], ignore_index=False, verify_integrity=False)
combined_location_dataframe

Borough                                       Neighborhood  \
0       East Toronto                                        The Beaches   
1       East Toronto                       The Danforth West, Riverdale   
2       East Toronto                     The Beaches West, India Bazaar   
3       East Toronto                                    Studio District   
4    Central Toronto                                      Lawrence Park   
5    Central Toronto                                   Davisville North   
6    Central Toronto                                 North Toronto West   
7    Central Toronto                                         Davisville   
8    Central Toronto                        Moore Park, Summerhill East   
9    Central Toronto  Deer Park, Forest Hill SE, Rathnelly, South Hi...   
10  Downtown Toronto                                           Rosedale   
11  Downtown Toronto                        Cabbagetown, St. James Town   
12  Downtown Toronto                               Church and Wellesley   
13  Downtown Toronto                          Harbourfront, Regent Park   
14  Downtown Toronto                           Ryerson, Garden District   
15  Downtown Toronto                                     St. James Town   
16  Downtown Toronto                                        Berczy Park   
17  Downtown Toronto                                 Central Bay Street   
18  Downtown Toronto                           Adelaide, King, Richmond   
19  Downtown Toronto  Harbourfront East, Toronto Islands, Union Station   
20  Downtown Toronto           Design Exchange, Toronto Dominion Centre   
21  Downtown Toronto                     Commerce Court, Victoria Hotel   
22   Central Toronto                                           Roselawn   
23   Central Toronto                Forest Hill North, Forest Hill West   
24   Central Toronto                The Annex, North Midtown, Yorkville   
25  Downtown Toronto                     Harbord, University of Toronto   
26  Downtown Toronto          Chinatown, Grange Park, Kensington Market   
27  Downtown Toronto  CN Tower, Bathurst Quay, Island airport, Harbo...   
28  Downtown Toronto                    Stn A PO Boxes 25 The Esplanade   
29  Downtown Toronto             First Canadian Place, Underground city   
30  Downtown Toronto                                           Christie   
31      West Toronto                       Dovercourt Village, Dufferin   
32      West Toronto                           Little Portugal, Trinity   
33      West Toronto       Brockton, Exhibition Place, Parkdale Village   
34      West Toronto                      High Park, The Junction South   
35      West Toronto                             Parkdale, Roncesvalles   
36      West Toronto                                 Runnymede, Swansea   
37      East Toronto  Business Reply Mail Processing Centre 969 Eastern   
0          Manhattan                                        Marble Hill   
1          Manhattan                                          Chinatown   
2          Manhattan                                 Washington Heights   
3          Manhattan                                             Inwood   
4          Manhattan                                   Hamilton Heights   
5          Manhattan                                     Manhattanville   
6          Manhattan                                     Central Harlem   
7          Manhattan                                        East Harlem   
8          Manhattan                                    Upper East Side   
9          Manhattan                                          Yorkville   
10         Manhattan                                         Lenox Hill   
11         Manhattan                                   Roosevelt Island   
12         Manhattan                                    Upper West Side   
13         Manhattan                                     Lincoln Square   
14         Manhattan                  

Now I will add the latitude and longitude information to the dataframe with the cluster labels.

In [91]:
combined_sorted_venues_with_location_data = combined_sorted_venues.join(combined_location_dataframe.set_index('Neighborhood'), on='Neighborhood', how = 'left')

combined_sorted_venues_with_location_data

Cluster Labels                                       Neighborhood  \
0                3                                  Battery Park City   
1                1                                      Carnegie Hill   
2                0                                     Central Harlem   
3                1                                            Chelsea   
4                0                                          Chinatown   
5                0                                       Civic Center   
6                1                                            Clinton   
7                4                                        East Harlem   
8                1                                       East Village   
9                1                                 Financial District   
10               0                                           Flatiron   
11               1                                           Gramercy   
12               0                                  Greenwich Village   
13               4                                   Hamilton Heights   
14               0                                       Hudson Yards   
15               4                                             Inwood   
16               1                                         Lenox Hill   
17               0                                     Lincoln Square   
18               0                                       Little Italy   
19               4                                    Lower East Side   
20               1                                   Manhattan Valley   
21               4                                     Manhattanville   
22               4                                        Marble Hill   
23               0                                            Midtown   
24               1                                      Midtown South   
25               3                                Morningside Heights   
26               1                                        Murray Hill   
27               1                                               Noho   
28               3                                   Roosevelt Island   
29               0                                               Soho   
30               2                                    Stuyvesant Town   
31               1                                       Sutton Place   
32               0                                            Tribeca   
33               4                                         Tudor City   
34               0                                         Turtle Bay   
35               0                                    Upper East Side   
36               1                                    Upper West Side   
37               4                                 Washington Heights   
38               0                                       West Village   
39               1                                          Yorkville   
40               3                           Adelaide, King, Richmond   
41               3                                        Berczy Park   
42               3       Brockton, Exhibition Place, Parkdale Village   
43               3  Business Reply Mail Processing Centre 969 Eastern   
44               3  CN Tower, Bathurst Quay, Island airport, Harbo...   
45               3                        Cabbagetown, St. James Town   
46               3                                 Central Bay Street   
47               3          Chinatown, Grange Park, Kensington Market   
48               3                                           Christie   
49               3                               Church and Wellesley   
50               3                     Commerce Court, Victoria Hotel   
51               3                                         Davisville   
52               3                                   Davisville North   
53               3  Deer Park, Forest Hill SE, Rathnelly, Sout

In [92]:
locations_merged = combined_sorted_venues_with_location_data 
locations_merged

Cluster Labels                                       Neighborhood  \
0                3                                  Battery Park City   
1                1                                      Carnegie Hill   
2                0                                     Central Harlem   
3                1                                            Chelsea   
4                0                                          Chinatown   
5                0                                       Civic Center   
6                1                                            Clinton   
7                4                                        East Harlem   
8                1                                       East Village   
9                1                                 Financial District   
10               0                                           Flatiron   
11               1                                           Gramercy   
12               0                                  Greenwich Village   
13               4                                   Hamilton Heights   
14               0                                       Hudson Yards   
15               4                                             Inwood   
16               1                                         Lenox Hill   
17               0                                     Lincoln Square   
18               0                                       Little Italy   
19               4                                    Lower East Side   
20               1                                   Manhattan Valley   
21               4                                     Manhattanville   
22               4                                        Marble Hill   
23               0                                            Midtown   
24               1                                      Midtown South   
25               3                                Morningside Heights   
26               1                                        Murray Hill   
27               1                                               Noho   
28               3                                   Roosevelt Island   
29               0                                               Soho   
30               2                                    Stuyvesant Town   
31               1                                       Sutton Place   
32               0                                            Tribeca   
33               4                                         Tudor City   
34               0                                         Turtle Bay   
35               0                                    Upper East Side   
36               1                                    Upper West Side   
37               4                                 Washington Heights   
38               0                                       West Village   
39               1                                          Yorkville   
40               3                           Adelaide, King, Richmond   
41               3                                        Berczy Park   
42               3       Brockton, Exhibition Place, Parkdale Village   
43               3  Business Reply Mail Processing Centre 969 Eastern   
44               3  CN Tower, Bathurst Quay, Island airport, Harbo...   
45               3                        Cabbagetown, St. James Town   
46               3                                 Central Bay Street   
47               3          Chinatown, Grange Park, Kensington Market   
48               3                                           Christie   
49               3                               Church and Wellesley   
50               3                     Commerce Court, Victoria Hotel   
51               3                                         Davisville   
52               3                                   Davisville North   
53               3  Deer Park, Forest Hill SE, Rathnelly, Sout

Now lets visualize the clusters on a map

In [93]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(locations_merged['Latitude'], locations_merged['Longitude'], locations_merged['Neighborhood'], locations_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Now let's look at each of the clusters.

In [94]:
locations_merged.loc[locations_merged['Cluster Labels'] == 0, locations_merged.columns[[1] + list(range(2, locations_merged.shape[1]))]]

Neighborhood 1st Most Common Venue    2nd Most Common Venue  \
2      Central Harlem    African Restaurant       Chinese Restaurant   
4           Chinatown    Chinese Restaurant      American Restaurant   
5        Civic Center    Italian Restaurant     Gym / Fitness Center   
10           Flatiron                   Gym              Yoga Studio   
12  Greenwich Village    Italian Restaurant           Clothing Store   
14       Hudson Yards   American Restaurant       Italian Restaurant   
17     Lincoln Square               Theater     Gym / Fitness Center   
18       Little Italy                Bakery           Clothing Store   
23            Midtown                 Hotel              Coffee Shop   
29               Soho        Clothing Store                 Boutique   
32            Tribeca                   Spa                     Café   
34         Turtle Bay    Italian Restaurant                    Hotel   
35    Upper East Side    Italian Restaurant                  Exhibit   
38       West Village    Italian Restaurant  New American Restaurant   
68           Roselawn        Ice Cream Shop                   Garden   

   3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  \
2      French Restaurant        Cosmetics Shop       American Restaurant   
4           Cocktail Bar   Dumpling Restaurant           Bubble Tea Shop   
5                 Bakery           Coffee Shop         French Restaurant   
10  Gym / Fitness Center   American Restaurant       Japanese Restaurant   
12      Sushi Restaurant     French Restaurant                      Café   
14           Coffee Shop                  Café                   Theater   
17          Concert Hall                  Café                     Plaza   
18        Sandwich Place    Salon / Barbershop  Mediterranean Restaurant   
23               Theater          Cocktail Bar            Clothing Store   
29            Shoe Store         Women's Store               Men's Store   
32    Italian Restaurant              Boutique       American Restaurant   
34      Sushi Restaurant            Steakhouse               Coffee Shop   
35           Coffee Shop                Bakery      Gym / Fitness Center   
38        Cosmetics Shop             Jazz Club                      Park   
68         Women's Store        Discount Store      Fast Food Restaurant   

   6th Most Common Venue  7th Most Common Venue    8th Most Common Venue  \
2          Deli / Bodega     Seafood Restaurant     Gym / Fitness Center   
4                    Spa  Vietnamese Restaurant       Salon / Barbershop   
5         Sandwich Place            Yoga Studio             Cocktail Bar   
10                  Café         Clothing Store  New American Restaurant   
12    Seafood Restaurant      Indian Restaurant           Ice Cream Shop   
14  Gym / Fitness Center                  Hotel           Ice Cream Shop   
17    Italian Restaurant            Opera House    Performing Arts Venue   
18    Italian Restaurant     Seafood Restaurant                    Hotel   
23   Sporting Goods Shop    American Restaurant      Japanese Restaurant   
29   Sporting Goods Shop            Art Gallery                   Bakery   
32                  Park                    Gym                 Wine Bar   
34              Wine Bar                   Park        French Restaurant   
35           Art Gallery              Juice Bar                    Hotel   
38              Wine Bar    American Restaurant                   Bakery   
68        Farmers Market     Falafel Restaurant              Event Space   

   9th Most Common Venue    10th Most Common Venue          Borough  \
2             Public Art                   Library        Manhattan   
4      Hotpot Restaurant    Furniture / Home Store        Manhattan   
5                   Park       Sporting Goods Shop        Manhattan   
10                   Spa            Cosmetics Shop        Manhattan   
12           Coffee Shop                       Spa        Manhattan

In [95]:
locations_merged.loc[locations_merged['Cluster Labels'] == 1, locations_merged.columns[[1] + list(range(2, locations_merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
1                         Carnegie Hill           Coffee Shop   
3                               Chelsea           Coffee Shop   
6                               Clinton               Theater   
8                          East Village                   Bar   
9                    Financial District           Coffee Shop   
11                             Gramercy   American Restaurant   
16                           Lenox Hill           Coffee Shop   
20                     Manhattan Valley     Indian Restaurant   
24                        Midtown South     Korean Restaurant   
26                          Murray Hill                 Hotel   
27                                 Noho    Italian Restaurant   
31                         Sutton Place    Italian Restaurant   
36                      Upper West Side    Italian Restaurant   
39                            Yorkville    Italian Restaurant   
57  Forest Hill North, Forest Hill West                  Park   
64          Moore Park, Summerhill East            Playground   
67                             Rosedale                  Park   

   2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
1            Pizza Place                  Café             Yoga Studio   
3         Ice Cream Shop    Italian Restaurant                  Bakery   
6   Gym / Fitness Center   American Restaurant      Italian Restaurant   
8               Wine Bar        Ice Cream Shop      Mexican Restaurant   
9             Steakhouse                   Gym               Wine Shop   
11    Italian Restaurant            Bagel Shop                     Bar   
16    Italian Restaurant      Sushi Restaurant             Pizza Place   
20           Coffee Shop           Pizza Place             Yoga Studio   
24                 Hotel             Hotel Bar             Coffee Shop   
26        Sandwich Place   Japanese Restaurant             Coffee Shop   
27     French Restaurant          Cocktail Bar      Mexican Restaurant   
31  Gym / Fitness Center     Indian Restaurant  Furniture / Home Store   
36              Wine Bar                   Bar             Coffee Shop   
39           Coffee Shop                   Gym                     Bar   
57                 Trail      Sushi Restaurant           Jewelry Store   
64                  Park          Tennis Court                   Trail   
67            Playground                 Trail           Women's Store   

       5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
1        Japanese Restaurant             Bookstore                   Bar   
3                  Nightclub   American Restaurant    Seafood Restaurant   
6                      Hotel             Wine Shop           Coffee Shop   
8         Chinese Restaurant          Cocktail Bar           Pizza Place   
9                      Hotel                  Park           Pizza Place   
11               Pizza Place          Cocktail Bar         Grocery Store   
16       Sporting Goods Shop          Burger Joint                   Gym   
20                       Bar   Szechuan Restaurant       Thai Restaurant   
24       Japanese Restaurant  Gym / Fitness Center        Cosmetics Shop   
26        Italian Restaurant    Salon / Barbershop     French Restaurant   
27                  Boutique           Art Gallery             Rock Club   
31       American Restaurant           Pizza Place             Juice Bar   
36  Mediterranean Restaurant                Bakery     Indian Restaurant   
39               Pizza Place      Sushi Restaurant        Ice Cream Shop   
57             Women's Store        Discount Store        Farmers Market   
64             Women's Store   Dumpling Restaurant        Discount Store   
67              Dessert Shop    Falafel Restaurant           Event Space   

            8th Most Common Venue 9th Most Common Venue  \
1                  Cosmetics Shop     French Restaurant   
3                           Hotel   

In [96]:
locations_merged.loc[locations_merged['Cluster Labels'] == 2, locations_merged.columns[[1] + list(range(2, locations_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
30  Stuyvesant Town                   Bar                  Park   
62    Lawrence Park                  Park           Swim School   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
30            Playground              Fountain     German Restaurant   
62              Bus Line         Women's Store        Discount Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
30        Baseball Field       Harbor / Marina          Cocktail Bar   
62        Farmers Market    Falafel Restaurant           Event Space   

   9th Most Common Venue 10th Most Common Venue          Borough  Latitude  \
30           Coffee Shop         Farmers Market        Manhattan  40.73100   
62  Ethiopian Restaurant      Electronics Store  Central Toronto  43.72802   

    Longitude  
30 -73.974052  
62 -79.388790

In [97]:
locations_merged.loc[locations_merged['Cluster Labels'] == 3, locations_merged.columns[[1] + list(range(2, locations_merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
0                                   Battery Park City                  Park   
25                                Morningside Heights             Bookstore   
28                                   Roosevelt Island           Coffee Shop   
40                           Adelaide, King, Richmond           Coffee Shop   
41                                        Berczy Park           Coffee Shop   
42       Brockton, Exhibition Place, Parkdale Village        Breakfast Spot   
43  Business Reply Mail Processing Centre 969 Eastern    Light Rail Station   
44  CN Tower, Bathurst Quay, Island airport, Harbo...       Airport Service   
45                        Cabbagetown, St. James Town           Coffee Shop   
46                                 Central Bay Street           Coffee Shop   
47          Chinatown, Grange Park, Kensington Market                  Café   
48                                           Christie         Grocery Store   
49                               Church and Wellesley           Coffee Shop   
50                     Commerce Court, Victoria Hotel           Coffee Shop   
51                                         Davisville           Pizza Place   
52                                   Davisville North        Breakfast Spot   
53  Deer Park, Forest Hill SE, Rathnelly, South Hi...           Coffee Shop   
54           Design Exchange, Toronto Dominion Centre           Coffee Shop   
55                       Dovercourt Village, Dufferin              Pharmacy   
56             First Canadian Place, Underground city           Coffee Shop   
58                     Harbord, University of Toronto                  Café   
59  Harbourfront East, Toronto Islands, Union Station           Coffee Shop   
60                          Harbourfront, Regent Park           Coffee Shop   
61                      High Park, The Junction South    Mexican Restaurant   
63                           Little Portugal, Trinity                   Bar   
65                                 North Toronto West        Clothing Store   
66                             Parkdale, Roncesvalles        Breakfast Spot   
69                                 Runnymede, Swansea           Pizza Place   
70                           Ryerson, Garden District           Coffee Shop   
71                                     St. James Town           Coffee Shop   
72                    Stn A PO Boxes 25 The Esplanade           Coffee Shop   
73                                    Studio District                  Café   
74                The Annex, North Midtown, Yorkville           Coffee Shop   
76                     The Beaches West, India Bazaar        Sandwich Place   
77                       The Danforth West, Riverdale      Greek Restaurant   

            2nd Most Common Venue 3rd Most Common Venue  \
0                     Coffee Shop                 Hotel   
25            American Restaurant           Coffee Shop   
28                           Park        Sandwich Place   
40                           Café            Steakhouse   
41                   Cocktail Bar    Italian Restaurant   
42                           Café           Coffee Shop   
43                    Pizza Place                Garden   
44                 Airport Lounge      Airport Terminal   
45                           Park            Restaurant   
46                           Café    Italian Restaurant   
47  Vegetarian / Vegan Restaurant           Coffee Shop   
48                           Café                  Park   
49            Japanese Restaurant      Sushi Restaurant   
50                           Café                 Hotel   
51                   Dessert Shop        Sandwich Place   
52                 Sandwich Place                   Gym   
53                            Pub           Pizza Place   
54                           Café                 Hotel   
55                         Bakery           Supermarket   
56              

In [99]:
locations_merged.loc[locations_merged['Cluster Labels'] == 4, locations_merged.columns[[1] + list(range(2, locations_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
7          East Harlem         Deli / Bodega    Mexican Restaurant   
13    Hamilton Heights                  Café           Pizza Place   
15              Inwood                  Café    Mexican Restaurant   
19     Lower East Side      Ramen Restaurant           Coffee Shop   
21      Manhattanville                  Park    Mexican Restaurant   
22         Marble Hill        Sandwich Place           Coffee Shop   
33          Tudor City                  Park    Mexican Restaurant   
37  Washington Heights                  Café     Mobile Phone Shop   
75         The Beaches     Health Food Store         Grocery Store   

   3rd Most Common Venue 4th Most Common Venue      5th Most Common Venue  \
7                 Bakery           Coffee Shop                        Spa   
13    Mexican Restaurant           Coffee Shop                Yoga Studio   
15                Lounge           Pizza Place                     Bakery   
19                  Café           Pizza Place         Chinese Restaurant   
21           Coffee Shop    Italian Restaurant         Seafood Restaurant   
22        Discount Store           Yoga Studio                      Diner   
33      Greek Restaurant                  Café           Asian Restaurant   
37                Bakery       Supplement Shop  Latin American Restaurant   
75            Astrologer                   Pub              Women's Store   

      6th Most Common Venue      7th Most Common Venue 8th Most Common Venue  \
7           Thai Restaurant  Latin American Restaurant        Sandwich Place   
13         Sushi Restaurant       Caribbean Restaurant    Chinese Restaurant   
15       Frozen Yogurt Shop         Chinese Restaurant                  Park   
19              Art Gallery                     Bakery   Japanese Restaurant   
21         Cuban Restaurant               Music School                Lounge   
22               Steakhouse            Supplement Shop    Seafood Restaurant   
33            Deli / Bodega                Pizza Place                 Hotel   
37  New American Restaurant         Chinese Restaurant    Mexican Restaurant   
75      Dumpling Restaurant             Discount Store               Dog Run   

   9th Most Common Venue 10th Most Common Venue       Borough   Latitude  \
7                   Bank               Beer Bar     Manhattan  40.792249   
13                Bakery                 School     Manhattan  40.823604   
15   American Restaurant          Deli / Bodega     Manhattan  40.867684   
19          Cocktail Bar         Sandwich Place     Manhattan  40.717807   
21            Bike Trail       Sushi Restaurant     Manhattan  40.816934   
22        Tennis Stadium                    Gym     Manhattan  40.876551   
33               Dog Run     Spanish Restaurant     Manhattan  40.746917   
37        Clothing Store            Supermarket     Manhattan  40.851903   
75      Doner Restaurant             Donut Shop  East Toronto  43.676357   

    Longitude  
7  -73.944182  
13 -73.949688  
15 -73.921210  
19 -73.980890  
21 -73.957385  
22 -73.910660  
33 -73.971219  
37 -73.936900  
75 -79.293031